In [1]:
import sklearn
from sklearn import datasets
from sklearn.utils import Bunch
import numpy as np
import pandas as pd
import pickle

In [2]:
pd.set_option('display.max_columns', None)  # or 1000

In [3]:
nbin = 5

In [4]:
def concat_onehot_cols(cols, bin_edges_):
    new_cols = []
    for i,c in enumerate(cols):
        l = bin_edges_[i]
        new_cols = new_cols + ['{}=[{:.2f}-{:.2f}]'.format(c, l[j], l[j+1]) for j in range(len(l)-1)]
    return new_cols


def preprocess(data, exclude_cols=[]):
    if len(exclude_cols) > 0:
        data.data = data.data.drop(exclude_cols, axis=1)
    print(data.data.shape)
    
    print("isnull: ", data.data[data.data.isnull().any(axis=1)].shape)
    print(data.data.isnull().any(axis=0)[data.data.isnull().any(axis=0)])
    
    data.target = data.target.astype('category')
    
    # Use 'categories' info
    if 'categories' in data:
        for c,v in data.categories.items():
            if c in exclude_cols: continue
            d = dict([(i,_) for i,_ in enumerate(v)])
            data.data[c] = data.data[c].astype('category').cat.codes.map(d).astype('category')
    
    # Impute NaN
    for c in data.data.select_dtypes(include='category').columns:
        data.data[c].fillna(data.data[c].mode()[0], inplace=True)
    for c in data.data.select_dtypes(exclude='category').columns:
        data.data[c].fillna(data.data[c].median(), inplace=True)
    
    print("isnull again: ", data.data[data.data.isnull().any(axis=1)].shape)
    print(data.data.isnull().any(axis=0)[data.data.isnull().any(axis=0)])

    
    cols_cat = data.data.select_dtypes(include=['category']).columns.tolist()
    cols_noncat = data.data.columns[~data.data.columns.isin(cols_cat)].tolist()
    cols_non2cat = []
    for c in cols_noncat:
        nu = data.data[c].unique().shape[0]
        if nu <= nbin:
            cols_non2cat.append(c)
            cols_cat.append(c)
    for c in cols_non2cat:
        cols_noncat.remove(c)
    cols_cat = pd.Index(cols_cat)
    cols_noncat = pd.Index(cols_noncat)

    df_cat = data.data[cols_cat]
    for c in cols_cat:
        dfc = df_cat[c].astype('category')
        df_cat = df_cat.drop(c, axis=1)
        if len(dfc.cat.categories) < 2:
            print(dfc)
        if len(dfc.cat.categories) == 2:
            df_cat = df_cat.join(pd.Series(dfc.cat.codes, name='{}={}'.format(c, dfc.cat.categories[1])))
        else:
            one_hot = pd.get_dummies(dfc, prefix=c, prefix_sep='=')
            df_cat = df_cat.join(one_hot)

    if len(cols_noncat) != 0:
        disc = sklearn.preprocessing.KBinsDiscretizer(n_bins=nbin, strategy='kmeans', encode='onehot-dense')
        data_noncat = disc.fit(data.data[cols_noncat]).transform(data.data[cols_noncat])
        new_cols_noncat = concat_onehot_cols(cols_noncat, disc.bin_edges_)
        df_noncat = pd.DataFrame(data_noncat.astype(int), columns=new_cols_noncat)
            
        df = pd.concat([df_cat,df_noncat], axis=1)    
    else:
        df = df_cat
    
    print(df.shape)
    return df, data.target

# iris

In [5]:
name = 'iris'

In [6]:
data = datasets.fetch_openml(name=name)

/Users/janfan/.pyenv/versions/anaconda3-2020.11/lib/python3.8/site-packages/sklearn/datasets/_openml.py:373: UserWarning: Multiple active versions of the dataset matching the name iris exist. Versions may be fundamentally different, returning version 1.
  warn("Multiple active versions of the dataset matching the name"


In [7]:
data

{'data': array([[5.1, 3.5, 1.4, 0.2],
        [4.9, 3. , 1.4, 0.2],
        [4.7, 3.2, 1.3, 0.2],
        [4.6, 3.1, 1.5, 0.2],
        [5. , 3.6, 1.4, 0.2],
        [5.4, 3.9, 1.7, 0.4],
        [4.6, 3.4, 1.4, 0.3],
        [5. , 3.4, 1.5, 0.2],
        [4.4, 2.9, 1.4, 0.2],
        [4.9, 3.1, 1.5, 0.1],
        [5.4, 3.7, 1.5, 0.2],
        [4.8, 3.4, 1.6, 0.2],
        [4.8, 3. , 1.4, 0.1],
        [4.3, 3. , 1.1, 0.1],
        [5.8, 4. , 1.2, 0.2],
        [5.7, 4.4, 1.5, 0.4],
        [5.4, 3.9, 1.3, 0.4],
        [5.1, 3.5, 1.4, 0.3],
        [5.7, 3.8, 1.7, 0.3],
        [5.1, 3.8, 1.5, 0.3],
        [5.4, 3.4, 1.7, 0.2],
        [5.1, 3.7, 1.5, 0.4],
        [4.6, 3.6, 1. , 0.2],
        [5.1, 3.3, 1.7, 0.5],
        [4.8, 3.4, 1.9, 0.2],
        [5. , 3. , 1.6, 0.2],
        [5. , 3.4, 1.6, 0.4],
        [5.2, 3.5, 1.5, 0.2],
        [5.2, 3.4, 1.4, 0.2],
        [4.7, 3.2, 1.6, 0.2],
        [4.8, 3.1, 1.6, 0.2],
        [5.4, 3.4, 1.5, 0.4],
        [5.2, 4.1, 1.5, 0.1],
  

In [8]:
data.data = pd.DataFrame(data.data, columns=data.feature_names)
data.target = pd.Series(data.target)

In [9]:
data.data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 150 entries, 0 to 149
Data columns (total 4 columns):
 #   Column       Non-Null Count  Dtype  
---  ------       --------------  -----  
 0   sepallength  150 non-null    float64
 1   sepalwidth   150 non-null    float64
 2   petallength  150 non-null    float64
 3   petalwidth   150 non-null    float64
dtypes: float64(4)
memory usage: 4.8 KB


In [10]:
X, Y = preprocess(data)
with open('dataset/{}.pkl'.format(name), 'wb') as f:
    pickle.dump((X, Y), f)

(150, 4)
isnull:  (0, 4)
Series([], dtype: bool)
isnull again:  (0, 4)
Series([], dtype: bool)
(150, 20)


In [11]:
X

sepallength=[4.30-5.24]  sepallength=[5.24-5.89]  \
0                          1                        0   
1                          1                        0   
2                          1                        0   
3                          1                        0   
4                          1                        0   
..                       ...                      ...   
145                        0                        0   
146                        0                        0   
147                        0                        0   
148                        0                        0   
149                        0                        0   

     sepallength=[5.89-6.46]  sepallength=[6.46-7.12]  \
0                          0                        0   
1                          0                        0   
2                          0                        0   
3                          0                        0   
4                          0                        0   
..                       ...                      ...   
145                        0                        1   
146                        1                        0   
147                        0                        1   
148                        1                        0   
149                        1                        0   

     sepallength=[7.12-7.90]  sepalwidth=[2.00-2.57]  sepalwidth=[2.57-2.96]  \
0                          0                       0                       0   
1                          0                       0                       0   
2                          0                       0                       0   
3                          0                       0                       0   
4                          0                       0                       0   
..                       ...                     ...                     ...   
145                        0                       0                       0   
146                        0                       1                       0   
147                        0                       0                       0   
148                        0                       0                       0   
149                        0                       0                       0   

     sepalwidth=[2.96-3.41]  sepalwidth=[3.41-3.92]  sepalwidth=[3.92-4.40]  \
0                         0                       1                       0   
1                         1                       0                       0   
2                         1                       0                       0   
3                         1                       0                       0   
4                         0                       1                       0   
..                      ...                     ...                     ...   
145                       1                       0                       0   
146                       0                       0                       0   
147                       1                       0                       0   
148                       1                       0                       0   
149                       1                       0                       0   

     petallength=[1.00-2.46]  petallength=[2.46-3.87]  \
0                          1                        0   
1                          1                        0   
2                          1                        0   
3                          1                        0   
4                          1                        0   
..                       ...                      ...   
145                        0                        0   
146                        0                        0   
147                        0                        0   
148                        0                        0   
149                        0                        0   

     petallength=[3.87-4.70]  petallengt

In [12]:
Y

0         Iris-setosa
1         Iris-setosa
2         Iris-setosa
3         Iris-setosa
4         Iris-setosa
            ...      
145    Iris-virginica
146    Iris-virginica
147    Iris-virginica
148    Iris-virginica
149    Iris-virginica
Length: 150, dtype: category
Categories (3, object): ['Iris-setosa', 'Iris-versicolor', 'Iris-virginica']

# breast-w

In [13]:
name = 'breast-w'

In [14]:
data = datasets.fetch_openml(name=name)

In [15]:
data

{'data': array([[ 5.,  1.,  1., ...,  3.,  1.,  1.],
        [ 5.,  4.,  4., ...,  3.,  2.,  1.],
        [ 3.,  1.,  1., ...,  3.,  1.,  1.],
        ...,
        [ 5., 10., 10., ...,  8., 10.,  2.],
        [ 4.,  8.,  6., ..., 10.,  6.,  1.],
        [ 4.,  8.,  8., ..., 10.,  4.,  1.]]),
 'target': array(['benign', 'benign', 'benign', 'benign', 'benign', 'malignant',
        'benign', 'benign', 'benign', 'benign', 'benign', 'benign',
        'malignant', 'benign', 'malignant', 'malignant', 'benign',
        'benign', 'malignant', 'benign', 'malignant', 'malignant',
        'benign', 'malignant', 'benign', 'malignant', 'benign', 'benign',
        'benign', 'benign', 'benign', 'benign', 'malignant', 'benign',
        'benign', 'benign', 'malignant', 'benign', 'malignant',
        'malignant', 'benign', 'malignant', 'malignant', 'malignant',
        'malignant', 'benign', 'malignant', 'benign', 'benign',
        'malignant', 'malignant', 'malignant', 'malignant', 'malignant',
        

In [16]:
data.data = pd.DataFrame(data.data, columns=data.feature_names)
data.target = pd.Series(data.target)

In [17]:
data.data

Clump_Thickness  Cell_Size_Uniformity  Cell_Shape_Uniformity  \
0                5.0                   1.0                    1.0   
1                5.0                   4.0                    4.0   
2                3.0                   1.0                    1.0   
3                6.0                   8.0                    8.0   
4                4.0                   1.0                    1.0   
..               ...                   ...                    ...   
694              3.0                   1.0                    1.0   
695              2.0                   1.0                    1.0   
696              5.0                  10.0                   10.0   
697              4.0                   8.0                    6.0   
698              4.0                   8.0                    8.0   

     Marginal_Adhesion  Single_Epi_Cell_Size  Bare_Nuclei  Bland_Chromatin  \
0                  1.0                   2.0          1.0              3.0   
1                  5.0                   7.0         10.0              3.0   
2                  1.0                   2.0          2.0              3.0   
3                  1.0                   3.0          4.0              3.0   
4                  3.0                   2.0          1.0              3.0   
..                 ...                   ...          ...              ...   
694                1.0                   3.0          2.0              1.0   
695                1.0                   2.0          1.0              1.0   
696                3.0                   7.0          3.0              8.0   
697                4.0                   3.0          4.0             10.0   
698                5.0                   4.0          5.0             10.0   

     Normal_Nucleoli  Mitoses  
0                1.0      1.0  
1                2.0      1.0  
2                1.0      1.0  
3                7.0      1.0  
4                1.0      1.0  
..               ...      ...  
694              1.0      1.0  
695              1.0      1.0  
696             10.0      2.0  
697              6.0      1.0  
698              4.0      1.0  

[699 rows x 9 columns]

In [18]:
data.data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 699 entries, 0 to 698
Data columns (total 9 columns):
 #   Column                 Non-Null Count  Dtype  
---  ------                 --------------  -----  
 0   Clump_Thickness        699 non-null    float64
 1   Cell_Size_Uniformity   699 non-null    float64
 2   Cell_Shape_Uniformity  699 non-null    float64
 3   Marginal_Adhesion      699 non-null    float64
 4   Single_Epi_Cell_Size   699 non-null    float64
 5   Bare_Nuclei            683 non-null    float64
 6   Bland_Chromatin        699 non-null    float64
 7   Normal_Nucleoli        699 non-null    float64
 8   Mitoses                699 non-null    float64
dtypes: float64(9)
memory usage: 49.3 KB


In [19]:
X, Y = preprocess(data)
with open('dataset/{}.pkl'.format(name), 'wb') as f:
    pickle.dump((X, Y), f)

(699, 9)
isnull:  (16, 9)
Bare_Nuclei    True
dtype: bool
isnull again:  (0, 9)
Series([], dtype: bool)
(699, 45)


In [20]:
X

Clump_Thickness=[1.00-2.34]  Clump_Thickness=[2.34-4.32]  \
0                              0                            0   
1                              0                            0   
2                              0                            1   
3                              0                            0   
4                              0                            1   
..                           ...                          ...   
694                            0                            1   
695                            1                            0   
696                            0                            0   
697                            0                            1   
698                            0                            1   

     Clump_Thickness=[4.32-6.44]  Clump_Thickness=[6.44-8.75]  \
0                              1                            0   
1                              1                            0   
2                              0                            0   
3                              1                            0   
4                              0                            0   
..                           ...                          ...   
694                            0                            0   
695                            0                            0   
696                            1                            0   
697                            0                            0   
698                            0                            0   

     Clump_Thickness=[8.75-10.00]  Cell_Size_Uniformity=[1.00-2.27]  \
0                               0                                 1   
1                               0                                 0   
2                               0                                 1   
3                               0                                 0   
4                               0                                 1   
..                            ...                               ...   
694                             0                                 1   
695                             0                                 1   
696                             0                                 0   
697                             0                                 0   
698                             0                                 0   

     Cell_Size_Uniformity=[2.27-4.45]  Cell_Size_Uniformity=[4.45-6.54]  \
0                                   0                                 0   
1                                   1                                 0   
2                                   0                                 0   
3                                   0                                 0   
4                                   0                                 0   
..                                ...                               ...   
694                                 0                                 0   
695                                 0                                 0   
696                                 0                                 0   
697                                 0                                 0   
698                                 0                                 0   

     Cell_Size_Uniformity=[6.54-8.76]  Cell_Size_Uniformity=[8.76-10.00]  \
0                                   0                                  0   
1                                   0                                  0   
2                                   0                                  0   
3                                   1                                  0   
4                                   0                                  0   
..                                ...                                ...   
694                                 0                                  0   
695                                 0                                  0   
696  

In [21]:
Y

0         benign
1         benign
2         benign
3         benign
4         benign
         ...    
694       benign
695       benign
696    malignant
697    malignant
698    malignant
Length: 699, dtype: category
Categories (2, object): ['benign', 'malignant']

# ilpd

In [22]:
name = 'ilpd'

In [23]:
data = datasets.fetch_openml(name=name)

In [24]:
data

{'data': array([[65.  ,  0.  ,  0.7 , ...,  6.8 ,  3.3 ,  0.9 ],
        [62.  ,  1.  , 10.9 , ...,  7.5 ,  3.2 ,  0.74],
        [62.  ,  1.  ,  7.3 , ...,  7.  ,  3.3 ,  0.89],
        ...,
        [52.  ,  1.  ,  0.8 , ...,  6.4 ,  3.2 ,  1.  ],
        [31.  ,  1.  ,  1.3 , ...,  6.8 ,  3.4 ,  1.  ],
        [38.  ,  1.  ,  1.  , ...,  7.3 ,  4.4 ,  1.5 ]]),
 'target': array(['1', '1', '1', '1', '1', '1', '1', '1', '2', '1', '1', '1', '2',
        '1', '1', '2', '1', '2', '1', '1', '1', '1', '1', '1', '2', '1',
        '1', '1', '2', '2', '1', '1', '2', '2', '2', '1', '2', '1', '1',
        '1', '1', '2', '2', '1', '2', '2', '1', '1', '1', '1', '1', '1',
        '1', '1', '1', '1', '2', '2', '1', '2', '1', '1', '1', '1', '1',
        '1', '1', '1', '1', '2', '1', '1', '1', '1', '1', '2', '1', '1',
        '2', '1', '1', '1', '2', '1', '1', '1', '2', '1', '1', '1', '1',
        '1', '1', '1', '1', '1', '1', '1', '1', '1', '2', '2', '1', '2',
        '1', '2', '2', '2', '2', '2', '2'

In [25]:
data.data = pd.DataFrame(data.data, columns=data.feature_names)
data.target = pd.Series(data.target)

In [26]:
data.data

V1   V2    V3   V4     V5    V6     V7   V8   V9   V10
0    65.0  0.0   0.7  0.1  187.0  16.0   18.0  6.8  3.3  0.90
1    62.0  1.0  10.9  5.5  699.0  64.0  100.0  7.5  3.2  0.74
2    62.0  1.0   7.3  4.1  490.0  60.0   68.0  7.0  3.3  0.89
3    58.0  1.0   1.0  0.4  182.0  14.0   20.0  6.8  3.4  1.00
4    72.0  1.0   3.9  2.0  195.0  27.0   59.0  7.3  2.4  0.40
..    ...  ...   ...  ...    ...   ...    ...  ...  ...   ...
578  60.0  1.0   0.5  0.1  500.0  20.0   34.0  5.9  1.6  0.37
579  40.0  1.0   0.6  0.1   98.0  35.0   31.0  6.0  3.2  1.10
580  52.0  1.0   0.8  0.2  245.0  48.0   49.0  6.4  3.2  1.00
581  31.0  1.0   1.3  0.5  184.0  29.0   32.0  6.8  3.4  1.00
582  38.0  1.0   1.0  0.3  216.0  21.0   24.0  7.3  4.4  1.50

[583 rows x 10 columns]

In [27]:
X, Y = preprocess(data)
with open('dataset/{}.pkl'.format(name), 'wb') as f:
    pickle.dump((X, Y), f)

(583, 10)
isnull:  (0, 10)
Series([], dtype: bool)
isnull again:  (0, 10)
Series([], dtype: bool)
(583, 46)


In [28]:
X

V2=Male  V1=[4.00-25.44]  V1=[25.44-39.56]  V1=[39.56-53.17]  \
0          0                0                 0                 0   
1          1                0                 0                 0   
2          1                0                 0                 0   
3          1                0                 0                 0   
4          1                0                 0                 0   
..       ...              ...               ...               ...   
578        1                0                 0                 0   
579        1                0                 0                 1   
580        1                0                 0                 1   
581        1                0                 1                 0   
582        1                0                 1                 0   

     V1=[53.17-66.61]  V1=[66.61-90.00]  V3=[0.40-4.32]  V3=[4.32-12.69]  \
0                   1                 0               1                0   
1                   1                 0               0                1   
2                   1                 0               0                1   
3                   1                 0               1                0   
4                   0                 1               1                0   
..                ...               ...             ...              ...   
578                 1                 0               1                0   
579                 0                 0               1                0   
580                 0                 0               1                0   
581                 0                 0               1                0   
582                 0                 0               1                0   

     V3=[12.69-24.19]  V3=[24.19-52.69]  V3=[52.69-75.00]  V4=[0.10-1.86]  \
0                   0                 0                 0               1   
1                   0                 0                 0               0   
2                   0                 0                 0               0   
3                   0                 0                 0               1   
4                   0                 0                 0               0   
..                ...               ...               ...             ...   
578                 0                 0                 0               1   
579                 0                 0                 0               1   
580                 0                 0                 0               1   
581                 0                 0                 0               1   
582                 0                 0                 0               1   

     V4=[1.86-5.67]  V4=[5.67-10.08]  V4=[10.08-15.23]  V4=[15.23-19.70]  \
0                 0                0                 0                 0   
1                 1                0                 0                 0   
2                 1                0                 0                 0   
3                 0                0                 0                 0   
4                 1                0                 0                 0   
..              ...              ...               ...               ...   
578               0                0                 0                 0   
579               0                0                 0                 0   
580               0                0                 0                 0   
581               0                0                 0                 0   
582               0                0                 0                 0   

     V5=[63.00-333.41]  V5=[333.41-650.13]  V5=[650.13-1169.17]  \
0                    1                   0                    0   
1                    0                   0                    1   
2                    0                   1                    0   
3                    1                   0                    0   
4                    1                   0                    0   
..                 ... 

In [29]:
Y

0      1
1      1
2      1
3      1
4      1
      ..
578    2
579    1
580    1
581    1
582    2
Length: 583, dtype: category
Categories (2, object): ['1', '2']

# Covertype

In [30]:
name = 'covertype'

In [31]:
data = datasets.fetch_openml(name=name)

/Users/janfan/.pyenv/versions/anaconda3-2020.11/lib/python3.8/site-packages/sklearn/datasets/_openml.py:373: UserWarning: Multiple active versions of the dataset matching the name covertype exist. Versions may be fundamentally different, returning version 3.
  warn("Multiple active versions of the dataset matching the name"


In [32]:
data

{'data': array([[0.368684, 0.141667, 0.045455, ..., 0.      , 0.      , 0.      ],
        [0.365683, 0.155556, 0.030303, ..., 0.      , 0.      , 0.      ],
        [0.472736, 0.386111, 0.136364, ..., 0.      , 0.      , 0.      ],
        ...,
        [0.263632, 0.441667, 0.257576, ..., 0.      , 0.      , 0.      ],
        [0.262631, 0.472222, 0.227273, ..., 0.      , 0.      , 0.      ],
        [0.262131, 0.458333, 0.19697 , ..., 0.      , 0.      , 0.      ]]),
 'target': array(['5', '5', '2', ..., '3', '3', '3'], dtype=object),
 'frame': None,
 'categories': {'Wilderness_Area1': ['0', '1'],
  'Wilderness_Area2': ['0', '1'],
  'Wilderness_Area3': ['0', '1'],
  'Wilderness_Area4': ['0', '1'],
  'Soil_Type1': ['0', '1'],
  'Soil_Type2': ['0', '1'],
  'Soil_Type3': ['0', '1'],
  'Soil_Type4': ['0', '1'],
  'Soil_Type5': ['0', '1'],
  'Soil_Type6': ['0', '1'],
  'Soil_Type7': ['0', '1'],
  'Soil_Type8': ['0', '1'],
  'Soil_Type9': ['0', '1'],
  'Soil_Type10': ['0', '1'],
  'Soil_Typ

In [33]:
data.data = pd.DataFrame(data.data, columns=data.feature_names)
data.target = pd.Series(data.target)

In [34]:
data.data

Elevation    Aspect     Slope  Horizontal_Distance_To_Hydrology  \
0        0.368684  0.141667  0.045455                          0.184681   
1        0.365683  0.155556  0.030303                          0.151754   
2        0.472736  0.386111  0.136364                          0.191840   
3        0.463232  0.430556  0.272727                          0.173228   
4        0.368184  0.125000  0.030303                          0.109520   
...           ...       ...       ...                               ...   
581007   0.268634  0.425000  0.303030                          0.060845   
581008   0.266133  0.422222  0.287879                          0.047960   
581009   0.263632  0.441667  0.257576                          0.042949   
581010   0.262631  0.472222  0.227273                          0.042949   
581011   0.262131  0.458333  0.196970                          0.042949   

        Vertical_Distance_To_Hydrology  Horizontal_Distance_To_Roadways  \
0                             0.223514                         0.071659   
1                             0.215762                         0.054798   
2                             0.307494                         0.446817   
3                             0.375969                         0.434172   
4                             0.222222                         0.054939   
...                                ...                              ...   
581007                        0.245478                         0.015175   
581008                        0.239018                         0.013348   
581009                        0.232558                         0.012646   
581010                        0.229974                         0.012646   
581011                        0.228682                         0.009414   

        Hillshade_9am  Hillshade_Noon  Hillshade_3pm  \
0            0.870079        0.913386       0.582677   
1            0.866142        0.925197       0.594488   
2            0.921260        0.937008       0.531496   
3            0.937008        0.937008       0.480315   
4            0.866142        0.921260       0.590551   
...               ...             ...            ...   
581007       0.944882        0.933071       0.464567   
581008       0.944882        0.933071       0.468504   
581009       0.929134        0.948819       0.511811   
581010       0.905512        0.964567       0.562992   
581011       0.909449        0.960630       0.555118   

        Horizontal_Distance_To_Fire_Points  Wilderness_Area1  \
0                                 0.875366               1.0   
1                                 0.867838               1.0   
2                                 0.853339               1.0   
3                                 0.865886               1.0   
4                                 0.860449               1.0   
...                                    ...               ...   
581007                            0.116688               0.0   
581008                            0.117803               0.0   
581009                            0.119058               0.0   
581010                            0.120452               0.0   
581011                            0.121985               0.0   

        Wilderness_Area2  Wilderness_Area3  Wilderness_Area4  Soil_Type1  \
0                    0.0               0.0               0.0         0.0   
1                    0.0               0.0               0.0         0.0   
2                    0.0               0.0               0.0         0.0   
3                    0.0               0.0               0.0         0.0   
4                    0.0               0.0               0.0         0.0   
...                  ...               ...               ...         ...   
581007               0.0               1.0               0.0         0.0   
581008               0.0               1.0               0.0         0.0   
581009               0.0               1.0               0.0         0.0   
5810

In [35]:
data.data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 581012 entries, 0 to 581011
Data columns (total 54 columns):
 #   Column                              Non-Null Count   Dtype  
---  ------                              --------------   -----  
 0   Elevation                           581012 non-null  float64
 1   Aspect                              581012 non-null  float64
 2   Slope                               581012 non-null  float64
 3   Horizontal_Distance_To_Hydrology    581012 non-null  float64
 4   Vertical_Distance_To_Hydrology      581012 non-null  float64
 5   Horizontal_Distance_To_Roadways     581012 non-null  float64
 6   Hillshade_9am                       581012 non-null  float64
 7   Hillshade_Noon                      581012 non-null  float64
 8   Hillshade_3pm                       581012 non-null  float64
 9   Horizontal_Distance_To_Fire_Points  581012 non-null  float64
 10  Wilderness_Area1                    581012 non-null  float64
 11  Wilderness_Area2          

In [36]:
X, Y = preprocess(data)
with open('dataset/covertype.pkl', 'wb') as f:
    pickle.dump((X, Y), f)

(581012, 54)
isnull:  (0, 54)
Series([], dtype: bool)
isnull again:  (0, 54)
Series([], dtype: bool)
(581012, 94)


In [37]:
X

Wilderness_Area1=1  Wilderness_Area2=1  Wilderness_Area3=1  \
0                        1                   0                   0   
1                        1                   0                   0   
2                        1                   0                   0   
3                        1                   0                   0   
4                        1                   0                   0   
...                    ...                 ...                 ...   
581007                   0                   0                   1   
581008                   0                   0                   1   
581009                   0                   0                   1   
581010                   0                   0                   1   
581011                   0                   0                   1   

        Wilderness_Area4=1  Soil_Type1=1  Soil_Type2=1  Soil_Type3=1  \
0                        0             0             0             0   
1                        0             0             0             0   
2                        0             0             0             0   
3                        0             0             0             0   
4                        0             0             0             0   
...                    ...           ...           ...           ...   
581007                   0             0             1             0   
581008                   0             0             1             0   
581009                   0             0             1             0   
581010                   0             0             1             0   
581011                   0             0             1             0   

        Soil_Type4=1  Soil_Type5=1  Soil_Type6=1  Soil_Type7=1  Soil_Type8=1  \
0                  0             0             0             0             0   
1                  0             0             0             0             0   
2                  0             0             0             0             0   
3                  0             0             0             0             0   
4                  0             0             0             0             0   
...              ...           ...           ...           ...           ...   
581007             0             0             0             0             0   
581008             0             0             0             0             0   
581009             0             0             0             0             0   
581010             0             0             0             0             0   
581011             0             0             0             0             0   

        Soil_Type9=1  Soil_Type10=1  Soil_Type11=1  Soil_Type12=1  \
0                  0              0              0              0   
1                  0              0              0              0   
2                  0              0              0              1   
3                  0              0              0              0   
4                  0              0              0              0   
...              ...            ...            ...            ...   
581007             0              0              0              0   
581008             0              0              0              0   
581009             0              0              0              0   
581010             0              0              0              0   
581011             0              0              0              0   

        Soil_Type13=1  Soil_Type14=1  Soil_Type15=1  Soil_Type16=1  \
0                   0              0              0              0   
1                   0              0              0              0   
2                   0              0              0              0   
3                   0              0              0              0   
4                   0              0              0              0   
...               ...            ...            ...            ...   
581007              0 

In [38]:
Y

0         5
1         5
2         2
3         2
4         5
         ..
581007    3
581008    3
581009    3
581010    3
581011    3
Length: 581012, dtype: category
Categories (7, object): ['1', '2', '3', '4', '5', '6', '7']

# tic-tac-toe

In [39]:
name = 'tic-tac-toe'

In [40]:
data = datasets.fetch_openml(name=name)

In [41]:
data

{'data': array([[2., 2., 2., ..., 2., 1., 1.],
        [2., 2., 2., ..., 1., 2., 1.],
        [2., 2., 2., ..., 1., 1., 2.],
        ...,
        [1., 2., 1., ..., 2., 1., 2.],
        [1., 2., 1., ..., 2., 1., 2.],
        [1., 1., 2., ..., 1., 2., 2.]]),
 'target': array(['positive', 'positive', 'positive', 'positive', 'positive',
        'positive', 'positive', 'positive', 'positive', 'positive',
        'positive', 'positive', 'positive', 'positive', 'positive',
        'positive', 'positive', 'positive', 'positive', 'positive',
        'positive', 'positive', 'positive', 'positive', 'positive',
        'positive', 'positive', 'positive', 'positive', 'positive',
        'positive', 'positive', 'positive', 'positive', 'positive',
        'positive', 'positive', 'positive', 'positive', 'positive',
        'positive', 'positive', 'positive', 'positive', 'positive',
        'positive', 'positive', 'positive', 'positive', 'positive',
        'positive', 'positive', 'positive', 'positive

In [42]:
data.data = pd.DataFrame(data.data, columns=data.feature_names)
data.target = pd.Series(data.target)

In [43]:
data.data

top-left-square  top-middle-square  top-right-square  middle-left-square  \
0                2.0                2.0               2.0                 2.0   
1                2.0                2.0               2.0                 2.0   
2                2.0                2.0               2.0                 2.0   
3                2.0                2.0               2.0                 2.0   
4                2.0                2.0               2.0                 2.0   
..               ...                ...               ...                 ...   
953              1.0                2.0               2.0                 2.0   
954              1.0                2.0               1.0                 2.0   
955              1.0                2.0               1.0                 2.0   
956              1.0                2.0               1.0                 1.0   
957              1.0                1.0               2.0                 2.0   

     middle-middle-square  middle-right-square  bottom-left-square  \
0                     1.0                  1.0                 2.0   
1                     1.0                  1.0                 1.0   
2                     1.0                  1.0                 1.0   
3                     1.0                  1.0                 1.0   
4                     1.0                  1.0                 0.0   
..                    ...                  ...                 ...   
953                   1.0                  1.0                 1.0   
954                   2.0                  1.0                 2.0   
955                   1.0                  2.0                 2.0   
956                   2.0                  2.0                 2.0   
957                   2.0                  1.0                 1.0   

     bottom-middle-square  bottom-right-square  
0                     1.0                  1.0  
1                     2.0                  1.0  
2                     1.0                  2.0  
3                     0.0                  0.0  
4                     1.0                  0.0  
..                    ...                  ...  
953                   2.0                  2.0  
954                   1.0                  2.0  
955                   1.0                  2.0  
956                   1.0                  2.0  
957                   2.0                  2.0  

[958 rows x 9 columns]

In [44]:
data.data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 958 entries, 0 to 957
Data columns (total 9 columns):
 #   Column                Non-Null Count  Dtype  
---  ------                --------------  -----  
 0   top-left-square       958 non-null    float64
 1   top-middle-square     958 non-null    float64
 2   top-right-square      958 non-null    float64
 3   middle-left-square    958 non-null    float64
 4   middle-middle-square  958 non-null    float64
 5   middle-right-square   958 non-null    float64
 6   bottom-left-square    958 non-null    float64
 7   bottom-middle-square  958 non-null    float64
 8   bottom-right-square   958 non-null    float64
dtypes: float64(9)
memory usage: 67.5 KB


In [45]:
X, Y = preprocess(data)
with open('dataset/{}.pkl'.format(name), 'wb') as f:
    pickle.dump((X, Y), f)

(958, 9)
isnull:  (0, 9)
Series([], dtype: bool)
isnull again:  (0, 9)
Series([], dtype: bool)
(958, 27)


In [46]:
X

top-left-square=b  top-left-square=o  top-left-square=x  \
0                    0                  0                  1   
1                    0                  0                  1   
2                    0                  0                  1   
3                    0                  0                  1   
4                    0                  0                  1   
..                 ...                ...                ...   
953                  0                  1                  0   
954                  0                  1                  0   
955                  0                  1                  0   
956                  0                  1                  0   
957                  0                  1                  0   

     top-middle-square=b  top-middle-square=o  top-middle-square=x  \
0                      0                    0                    1   
1                      0                    0                    1   
2                      0                    0                    1   
3                      0                    0                    1   
4                      0                    0                    1   
..                   ...                  ...                  ...   
953                    0                    0                    1   
954                    0                    0                    1   
955                    0                    0                    1   
956                    0                    0                    1   
957                    0                    1                    0   

     top-right-square=b  top-right-square=o  top-right-square=x  \
0                     0                   0                   1   
1                     0                   0                   1   
2                     0                   0                   1   
3                     0                   0                   1   
4                     0                   0                   1   
..                  ...                 ...                 ...   
953                   0                   0                   1   
954                   0                   1                   0   
955                   0                   1                   0   
956                   0                   1                   0   
957                   0                   0                   1   

     middle-left-square=b  middle-left-square=o  middle-left-square=x  \
0                       0                     0                     1   
1                       0                     0                     1   
2                       0                     0                     1   
3                       0                     0                     1   
4                       0                     0                     1   
..                    ...                   ...                   ...   
953                     0                     0                     1   
954                     0                     0                     1   
955                     0                     0                     1   
956                     0                     1                     0   
957                     0                     0                     1   

     middle-middle-square=b  middle-middle-square=o  middle-middle-square=x  \
0                         0                       1                       0   
1                         0                       1                       0   
2                         0                       1                       0   
3                         0                       1                       0   
4                         0                       1                       0   
..                      ...                     ...                     ...   
953                       0                       1                       0   
954                       0                       0                       1   
95

In [47]:
Y

0      positive
1      positive
2      positive
3      positive
4      positive
         ...   
953    negative
954    negative
955    negative
956    negative
957    negative
Length: 958, dtype: category
Categories (2, object): ['negative', 'positive']

# phoneme

In [48]:
name = 'phoneme'

In [49]:
data = datasets.fetch_openml(name=name)

In [50]:
data

{'data': array([[ 0.489927, -0.451528, -1.04799 , -0.598693, -0.020418],
        [-0.641265,  0.109245,  0.29213 , -0.916804,  0.240223],
        [ 0.870593, -0.459862,  0.578159,  0.806634,  0.835248],
        ...,
        [ 0.246882, -0.793228,  1.190101,  1.423194, -1.303036],
        [-0.778907, -0.383111,  1.727029, -1.432389, -1.208085],
        [-0.794604, -0.640053,  0.632221,  0.72028 , -1.231182]]),
 'target': array(['1', '1', '1', ..., '2', '1', '2'], dtype=object),
 'frame': None,
 'categories': {},
 'feature_names': ['V1', 'V2', 'V3', 'V4', 'V5'],
 'target_names': ['Class'],
 'DESCR': '**Author**: Dominique Van Cappel, THOMSON-SINTRA  \n**Source**: [KEEL](http://sci2s.ugr.es/keel/dataset.php?cod=105#sub2), [ELENA](https://www.elen.ucl.ac.be/neural-nets/Research/Projects/ELENA/databases/REAL/phoneme/) - 1993  \n**Please cite**: None  \n\nThe aim of this dataset is to distinguish between nasal (class 0) and oral sounds (class 1). Five different attributes were chosen to char

In [51]:
data.data = pd.DataFrame(data.data, columns=data.feature_names)
data.target = pd.Series(data.target)

In [52]:
data.data

V1        V2        V3        V4        V5
0     0.489927 -0.451528 -1.047990 -0.598693 -0.020418
1    -0.641265  0.109245  0.292130 -0.916804  0.240223
2     0.870593 -0.459862  0.578159  0.806634  0.835248
3    -0.628439 -0.316284  1.934295 -1.427099 -0.136583
4    -0.596399  0.015938  2.043206 -1.688448 -0.948127
...        ...       ...       ...       ...       ...
5399 -0.658318  1.331760 -0.081621  1.794253 -1.082181
5400 -0.044375 -0.010512  0.030989 -0.019379  1.281061
5401  0.246882 -0.793228  1.190101  1.423194 -1.303036
5402 -0.778907 -0.383111  1.727029 -1.432389 -1.208085
5403 -0.794604 -0.640053  0.632221  0.720280 -1.231182

[5404 rows x 5 columns]

In [53]:
data.data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5404 entries, 0 to 5403
Data columns (total 5 columns):
 #   Column  Non-Null Count  Dtype  
---  ------  --------------  -----  
 0   V1      5404 non-null   float64
 1   V2      5404 non-null   float64
 2   V3      5404 non-null   float64
 3   V4      5404 non-null   float64
 4   V5      5404 non-null   float64
dtypes: float64(5)
memory usage: 211.2 KB


In [54]:
X, Y = preprocess(data)
with open('dataset/{}.pkl'.format(name), 'wb') as f:
    pickle.dump((X, Y), f)

(5404, 5)
isnull:  (0, 5)
Series([], dtype: bool)
isnull again:  (0, 5)
Series([], dtype: bool)
(5404, 25)


In [55]:
X

V1=[-2.93--0.91]  V1=[-0.91--0.20]  V1=[-0.20-0.73]  V1=[0.73-1.91]  \
0                    0                 0                1               0   
1                    0                 1                0               0   
2                    0                 0                0               1   
3                    0                 1                0               0   
4                    0                 1                0               0   
...                ...               ...              ...             ...   
5399                 0                 1                0               0   
5400                 0                 0                1               0   
5401                 0                 0                1               0   
5402                 0                 1                0               0   
5403                 0                 1                0               0   

      V1=[1.91-3.83]  V2=[-3.04--1.38]  V2=[-1.38--0.42]  V2=[-0.42-0.42]  \
0                  0                 0                 1                0   
1                  0                 0                 0                1   
2                  0                 0                 1                0   
3                  0                 0                 0                1   
4                  0                 0                 0                1   
...              ...               ...               ...              ...   
5399               0                 0                 0                0   
5400               0                 0                 0                1   
5401               0                 0                 1                0   
5402               0                 0                 0                1   
5403               0                 0                 1                0   

      V2=[0.42-1.36]  V2=[1.36-3.66]  V3=[-2.80--0.82]  V3=[-0.82--0.10]  \
0                  0               0                 1                 0   
1                  0               0                 0                 0   
2                  0               0                 0                 0   
3                  0               0                 0                 0   
4                  0               0                 0                 0   
...              ...             ...               ...               ...   
5399               1               0                 0                 0   
5400               0               0                 0                 0   
5401               0               0                 0                 0   
5402               0               0                 0                 0   
5403               0               0                 0                 0   

      V3=[-0.10-0.55]  V3=[0.55-1.29]  V3=[1.29-2.63]  V4=[-2.49--0.97]  \
0                   0               0               0                 0   
1                   1               0               0                 0   
2                   0               1               0                 0   
3                   0               0               1                 1   
4                   0               0               1                 1   
...               ...             ...             ...               ...   
5399                1               0               0                 0   
5400                1               0               0                 0   
5401                0               1               0                 0   
5402                0               0               1                 1   
5403                0               1               0                 0   

      V4=[-0.97--0.29]  V4=[-0.29-0.47]  V4=[0.47-1.39]  V4=[1.39-3.05]  \
0                    1                0               0               0   
1                    1                0               0               0   
2                    0                0               1               0   
3                    0                0   

In [56]:
Y

0       1
1       1
2       1
3       1
4       1
       ..
5399    1
5400    2
5401    2
5402    1
5403    2
Length: 5404, dtype: category
Categories (2, object): ['1', '2']

# spambase

In [57]:
name = 'spambase'

In [58]:
data = datasets.fetch_openml(name=name)

In [59]:
data

{'data': array([[0.000e+00, 6.400e-01, 6.400e-01, ..., 3.756e+00, 6.100e+01,
         2.780e+02],
        [2.100e-01, 2.800e-01, 5.000e-01, ..., 5.114e+00, 1.010e+02,
         1.028e+03],
        [6.000e-02, 0.000e+00, 7.100e-01, ..., 9.821e+00, 4.850e+02,
         2.259e+03],
        ...,
        [3.000e-01, 0.000e+00, 3.000e-01, ..., 1.404e+00, 6.000e+00,
         1.180e+02],
        [9.600e-01, 0.000e+00, 0.000e+00, ..., 1.147e+00, 5.000e+00,
         7.800e+01],
        [0.000e+00, 0.000e+00, 6.500e-01, ..., 1.250e+00, 5.000e+00,
         4.000e+01]]),
 'target': array(['1', '1', '1', ..., '0', '0', '0'], dtype=object),
 'frame': None,
 'categories': {},
 'feature_names': ['word_freq_make',
  'word_freq_address',
  'word_freq_all',
  'word_freq_3d',
  'word_freq_our',
  'word_freq_over',
  'word_freq_remove',
  'word_freq_internet',
  'word_freq_order',
  'word_freq_mail',
  'word_freq_receive',
  'word_freq_will',
  'word_freq_people',
  'word_freq_report',
  'word_freq_addresses'

In [60]:
data.data = pd.DataFrame(data.data, columns=data.feature_names)
data.target = pd.Series(data.target)

In [61]:
data.data

word_freq_make  word_freq_address  word_freq_all  word_freq_3d  \
0               0.00               0.64           0.64           0.0   
1               0.21               0.28           0.50           0.0   
2               0.06               0.00           0.71           0.0   
3               0.00               0.00           0.00           0.0   
4               0.00               0.00           0.00           0.0   
...              ...                ...            ...           ...   
4596            0.31               0.00           0.62           0.0   
4597            0.00               0.00           0.00           0.0   
4598            0.30               0.00           0.30           0.0   
4599            0.96               0.00           0.00           0.0   
4600            0.00               0.00           0.65           0.0   

      word_freq_our  word_freq_over  word_freq_remove  word_freq_internet  \
0              0.32            0.00              0.00                0.00   
1              0.14            0.28              0.21                0.07   
2              1.23            0.19              0.19                0.12   
3              0.63            0.00              0.31                0.63   
4              0.63            0.00              0.31                0.63   
...             ...             ...               ...                 ...   
4596           0.00            0.31              0.00                0.00   
4597           0.00            0.00              0.00                0.00   
4598           0.00            0.00              0.00                0.00   
4599           0.32            0.00              0.00                0.00   
4600           0.00            0.00              0.00                0.00   

      word_freq_order  word_freq_mail  word_freq_receive  word_freq_will  \
0                0.00            0.00               0.00            0.64   
1                0.00            0.94               0.21            0.79   
2                0.64            0.25               0.38            0.45   
3                0.31            0.63               0.31            0.31   
4                0.31            0.63               0.31            0.31   
...               ...             ...                ...             ...   
4596             0.00            0.00               0.00            1.88   
4597             0.00            0.00               0.00            0.00   
4598             0.00            0.00               0.00            1.80   
4599             0.00            0.00               0.00            0.32   
4600             0.00            0.00               0.00            0.00   

      word_freq_people  word_freq_report  word_freq_addresses  word_freq_free  \
0                 0.00              0.00                 0.00            0.32   
1                 0.65              0.21                 0.14            0.14   
2                 0.12              0.00                 1.75            0.06   
3                 0.31              0.00                 0.00            0.31   
4                 0.31              0.00                 0.00            0.31   
...                ...               ...                  ...             ...   
4596              0.00              0.00                 0.00            0.00   
4597              0.00              0.00                 0.00            0.00   
4598              0.30              0.00                 0.00            0.00   
4599              0.00              0.00                 0.00            0.00   
4600              0.65              0.00                 0.00            0.00   

      word_freq_business  word_freq_email  word_freq_you  word_freq_credit  \
0                   0.00             1.29           1.93              0.00   
1                   0.07             0.28           3.47              0.00   
2                   0.06             1.03           1.36              0.32   
3                 

In [62]:
data.data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4601 entries, 0 to 4600
Data columns (total 57 columns):
 #   Column                      Non-Null Count  Dtype  
---  ------                      --------------  -----  
 0   word_freq_make              4601 non-null   float64
 1   word_freq_address           4601 non-null   float64
 2   word_freq_all               4601 non-null   float64
 3   word_freq_3d                4601 non-null   float64
 4   word_freq_our               4601 non-null   float64
 5   word_freq_over              4601 non-null   float64
 6   word_freq_remove            4601 non-null   float64
 7   word_freq_internet          4601 non-null   float64
 8   word_freq_order             4601 non-null   float64
 9   word_freq_mail              4601 non-null   float64
 10  word_freq_receive           4601 non-null   float64
 11  word_freq_will              4601 non-null   float64
 12  word_freq_people            4601 non-null   float64
 13  word_freq_report            4601 

In [63]:
X, Y = preprocess(data)
with open('dataset/{}.pkl'.format(name), 'wb') as f:
    pickle.dump((X, Y), f)

(4601, 57)
isnull:  (0, 57)
Series([], dtype: bool)
isnull again:  (0, 57)
Series([], dtype: bool)
(4601, 285)


In [64]:
X

word_freq_make=[0.00-0.21]  word_freq_make=[0.21-0.67]  \
0                              1                           0   
1                              0                           1   
2                              1                           0   
3                              1                           0   
4                              1                           0   
...                          ...                         ...   
4596                           0                           1   
4597                           1                           0   
4598                           0                           1   
4599                           0                           0   
4600                           1                           0   

      word_freq_make=[0.67-1.52]  word_freq_make=[1.52-3.12]  \
0                              0                           0   
1                              0                           0   
2                              0                           0   
3                              0                           0   
4                              0                           0   
...                          ...                         ...   
4596                           0                           0   
4597                           0                           0   
4598                           0                           0   
4599                           1                           0   
4600                           0                           0   

      word_freq_make=[3.12-4.54]  word_freq_address=[0.00-0.36]  \
0                              0                              0   
1                              0                              1   
2                              0                              1   
3                              0                              1   
4                              0                              1   
...                          ...                            ...   
4596                           0                              1   
4597                           0                              1   
4598                           0                              1   
4599                           0                              1   
4600                           0                              1   

      word_freq_address=[0.36-1.63]  word_freq_address=[1.63-4.82]  \
0                                 1                              0   
1                                 0                              0   
2                                 0                              0   
3                                 0                              0   
4                                 0                              0   
...                             ...                            ...   
4596                              0                              0   
4597                              0                              0   
4598                              0                              0   
4599                              0                              0   
4600                              0                              0   

      word_freq_address=[4.82-10.68]  word_freq_address=[10.68-14.28]  \
0                                  0                                0   
1                                  0                                0   
2                                  0                                0   
3                                  0                                0   
4                                  0                                0   
...                              ...                              ...   
4596                               0                                0   
4597                               0                                0   
4598                               0                                0   
4599                               0                                0   
4600               

In [65]:
Y

0       1
1       1
2       1
3       1
4       1
       ..
4596    0
4597    0
4598    0
4599    0
4600    0
Length: 4601, dtype: category
Categories (2, object): ['0', '1']

# musk

In [66]:
name = 'musk'

In [67]:
data = datasets.fetch_openml(name=name)

In [68]:
data

{'data': array([[ 101.,   46., -108., ...,  -50., -112.,   96.],
        [ 101.,   41., -188., ...,  -61., -136.,   79.],
        [ 101.,   46., -194., ...,  -67., -145.,   39.],
        ...,
        [   0.,   44., -102., ...,  -66., -144.,   -6.],
        [   0.,   51., -121., ...,  -44., -116.,  117.],
        [   0.,   51., -122., ...,  -44., -115.,  118.]]),
 'target': array(['1', '1', '1', ..., '0', '0', '0'], dtype=object),
 'frame': None,
 'categories': {'molecule_name': ['NON-MUSK-jp13',
   'NON-MUSK-jp10',
   'NON-MUSK-jf79',
   'NON-MUSK-jf18',
   'NON-MUSK-j97',
   'NON-MUSK-j96',
   'NON-MUSK-j90',
   'NON-MUSK-j84',
   'NON-MUSK-j83',
   'NON-MUSK-j81',
   'NON-MUSK-j148',
   'NON-MUSK-j147',
   'NON-MUSK-j146',
   'NON-MUSK-j130',
   'NON-MUSK-j129',
   'NON-MUSK-j100',
   'NON-MUSK-f209',
   'NON-MUSK-f164',
   'NON-MUSK-f161',
   'NON-MUSK-f150',
   'NON-MUSK-f146',
   'NON-MUSK-362',
   'NON-MUSK-361',
   'NON-MUSK-360',
   'NON-MUSK-358',
   'NON-MUSK-338',
   'NON-MU

In [69]:
data.data = pd.DataFrame(data.data, columns=data.feature_names)
data.target = pd.Series(data.target)

In [70]:
data.data

molecule_name    f1     f2     f3     f4     f5     f6     f7     f8  \
0             101.0  46.0 -108.0  -60.0  -69.0 -117.0   49.0   38.0 -161.0   
1             101.0  41.0 -188.0 -145.0   22.0 -117.0   -6.0   57.0 -171.0   
2             101.0  46.0 -194.0 -145.0   28.0 -117.0   73.0   57.0 -168.0   
3             101.0  41.0 -188.0 -145.0   22.0 -117.0   -7.0   57.0 -170.0   
4             101.0  41.0 -188.0 -145.0   22.0 -117.0   -7.0   57.0 -170.0   
...             ...   ...    ...    ...    ...    ...    ...    ...    ...   
6593            0.0  51.0 -123.0  -23.0 -108.0 -117.0  134.0 -160.0   82.0   
6594            0.0  44.0 -104.0  -19.0 -105.0 -117.0  142.0 -165.0   68.0   
6595            0.0  44.0 -102.0  -19.0 -104.0 -117.0   72.0 -165.0   65.0   
6596            0.0  51.0 -121.0  -23.0 -106.0 -117.0   63.0 -161.0   79.0   
6597            0.0  51.0 -122.0  -23.0 -106.0 -117.0  190.0 -161.0   80.0   

         f9    f10    f11    f12    f13    f14    f15    f16    f17    f18  \
0      -8.0    5.0 -323.0 -220.0 -113.0 -299.0 -283.0 -307.0  -31.0 -106.0   
1     -39.0 -100.0 -319.0 -111.0 -228.0 -281.0 -281.0 -300.0   54.0 -149.0   
2     -39.0  -22.0 -319.0 -111.0 -104.0 -283.0 -282.0 -303.0   52.0 -152.0   
3     -39.0  -99.0 -319.0 -111.0 -228.0 -282.0 -281.0 -301.0   54.0 -150.0   
4     -39.0  -99.0 -319.0 -111.0 -228.0 -282.0 -281.0 -301.0   54.0 -150.0   
...     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
6593 -230.0  -28.0 -150.0  -63.0  -55.0  -77.0 -108.0 -308.0 -221.0  -41.0   
6594 -225.0  -32.0 -124.0  -77.0  -43.0  -74.0 -100.0 -291.0 -215.0  -25.0   
6595 -219.0  -12.0 -107.0  -66.0  -58.0  -82.0  -77.0 -288.0 -214.0  -21.0   
6596 -224.0  -30.0 -129.0  -54.0  -60.0  -86.0  -88.0 -307.0 -221.0  -39.0   
6597 -227.0  -52.0 -139.0  -63.0  -51.0  -79.0  -99.0 -122.0 -220.0  -35.0   

        f19    f20    f21    f22    f23    f24    f25    f26    f27    f28  \
0    -227.0  -42.0  -59.0  -22.0  -67.0  189.0   81.0   17.0  -27.0  -89.0   
1     -98.0 -196.0  -27.0  -22.0    2.0   75.0   49.0  -34.0   45.0  -91.0   
2     -97.0 -225.0  -28.0  -22.0    2.0  179.0   49.0  -33.0   46.0  -88.0   
3     -98.0 -196.0  -28.0  -22.0    2.0   77.0   48.0  -34.0   46.0  -91.0   
4     -98.0 -196.0  -28.0  -22.0    2.0   78.0   48.0  -34.0   46.0  -91.0   
...     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
6593  -57.0   12.0 -112.0 -183.0 -198.0  -35.0  137.0 -198.0 -168.0 -153.0   
6594  -49.0    6.0 -121.0 -183.0 -201.0  -54.0  127.0 -204.0 -164.0 -160.0   
6595  -58.0  -32.0  -93.0 -183.0 -197.0  -71.0  218.0 -217.0 -164.0 -161.0   
6596  -58.0  -12.0  -86.0 -184.0 -180.0  -61.0  221.0 -211.0 -168.0 -154.0   
6597  -57.0    6.0 -104.0 -183.0 -196.0  -51.0   63.0 -204.0 -169.0 -154.0   

       f29    f30    f31    f32    f33    f34    f35    f36    f37    f38  \
0    -67.0  105.0 -116.0  124.0 -106.0    5.0 -120.0   63.0 -165.0   40.0   
1     32.0   95.0 -116.0   85.0  -23.0   42.0  -58.0   61.0 -171.0    2.0   
2     22.0   79.0 -116.0   19.0  -11.0    6.0  -38.0   71.0 -175.0    3.0   
3     32.0   94.0 -116.0   84.0  -23.0   41.0  -58.0   62.0 -171.0    3.0   
4     31.0   94.0 -116.0   84.0  -23.0   41.0  -58.0   62.0 -171.0    3.0   
...    ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
6593 -51.0  252.0 -108.0  135.0 -121.0  119.0 -120.0   73.0   28.0 -153.0   
6594 -41.0  255.0 -117.0 -104.0  -14.0  133.0 -157.0  141.0   46.0 -153.0   
6595 -59.0  243.0 -117.0 -103.0  -14.0  118.0 -157.0  140.0 -150.0 -153.0   
6596 -63.0  243.0 -107.0  136.0 -121.0  116.0 -122.0   73.0 -155.0 -153.0   
6597  63.0  128.0 -108.0  135.0 -121.0   42.0 -122.0   73.0  -90.0 -153.0   

        f39    f40    f41    f42    f43    f44    f45    f46    f47    f48  \
0     -27.0   68.0  -44.0   98.0  -33.0 -314.0 -282.0 -335.0 -144.0  -13.0   
1    -144.0   38.0 -153.0  113.0 -166.0 -318.0 -241.0 -329.0  -97.0  -69.0   
2    -129.0   37.0 -172.0   93.0  -4

In [71]:
data.data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 6598 entries, 0 to 6597
Columns: 167 entries, molecule_name to f166
dtypes: float64(167)
memory usage: 8.4 MB


In [72]:
X, Y = preprocess(data, exclude_cols = ['molecule_name'])
with open('dataset/{}.pkl'.format(name), 'wb') as f:
    pickle.dump((X, Y), f)

(6598, 166)
isnull:  (0, 166)
Series([], dtype: bool)
isnull again:  (0, 166)
Series([], dtype: bool)
(6598, 830)


In [73]:
X

f1=[-31.00-26.09]  f1=[26.09-83.95]  f1=[83.95-171.10]  \
0                     0                 1                  0   
1                     0                 1                  0   
2                     0                 1                  0   
3                     0                 1                  0   
4                     0                 1                  0   
...                 ...               ...                ...   
6593                  0                 1                  0   
6594                  0                 1                  0   
6595                  0                 1                  0   
6596                  0                 1                  0   
6597                  0                 1                  0   

      f1=[171.10-253.52]  f1=[253.52-292.00]  f2=[-199.00--154.40]  \
0                      0                   0                     0   
1                      0                   0                     1   
2                      0                   0                     1   
3                      0                   0                     1   
4                      0                   0                     1   
...                  ...                 ...                   ...   
6593                   0                   0                     0   
6594                   0                   0                     0   
6595                   0                   0                     0   
6596                   0                   0                     0   
6597                   0                   0                     0   

      f2=[-154.40--89.99]  f2=[-89.99--17.16]  f2=[-17.16-50.13]  \
0                       1                   0                  0   
1                       0                   0                  0   
2                       0                   0                  0   
3                       0                   0                  0   
4                       0                   0                  0   
...                   ...                 ...                ...   
6593                    1                   0                  0   
6594                    1                   0                  0   
6595                    1                   0                  0   
6596                    1                   0                  0   
6597                    1                   0                  0   

      f2=[50.13-95.00]  f3=[-167.00--123.52]  f3=[-123.52--72.54]  \
0                    0                     0                    0   
1                    0                     1                    0   
2                    0                     1                    0   
3                    0                     1                    0   
4                    0                     1                    0   
...                ...                   ...                  ...   
6593                 0                     0                    0   
6594                 0                     0                    0   
6595                 0                     0                    0   
6596                 0                     0                    0   
6597                 0                     0                    0   

      f3=[-72.54--15.24]  f3=[-15.24-22.65]  f3=[22.65-81.00]  \
0                      1                  0                 0   
1                      0                  0                 0   
2                      0                  0                 0   
3                      0                  0                 0   
4                      0                  0                 0   
...                  ...                ...               ...   
6593                   1                  0                 0   
6594                   1                  0                 0   
6595                   1                  0                 0   
6596                   1                  0                 0   
6597                   1           

In [74]:
Y

0       1
1       1
2       1
3       1
4       1
       ..
6593    0
6594    0
6595    0
6596    0
6597    0
Length: 6598, dtype: category
Categories (2, object): ['0', '1']

# SpeedDating

In [75]:
name = 'SpeedDating'

In [76]:
data = datasets.fetch_openml(name=name)

/Users/janfan/.pyenv/versions/anaconda3-2020.11/lib/python3.8/site-packages/sklearn/datasets/_openml.py:373: UserWarning: Multiple active versions of the dataset matching the name speeddating exist. Versions may be fundamentally different, returning version 1.
  warn("Multiple active versions of the dataset matching the name"


In [77]:
data

{'data': array([[ 0.,  1.,  0., ...,  0.,  0.,  0.],
        [ 0.,  1.,  0., ...,  0.,  0.,  1.],
        [ 1.,  1.,  0., ...,  0.,  1.,  1.],
        ...,
        [ 1., 21.,  1., ...,  0.,  0.,  0.],
        [ 1., 21.,  1., ...,  1.,  0.,  0.],
        [ 1., 21.,  1., ...,  1.,  0.,  0.]]),
 'target': array(['0', '0', '1', ..., '0', '0', '0'], dtype=object),
 'frame': None,
 'categories': {'has_null': ['0', '1'],
  'gender': ['female', 'male'],
  'd_d_age': ['[4-6]', '[0-1]', '[2-3]', '[7-37]'],
  'race': ['Asian/Pacific Islander/Asian-American',
   'European/Caucasian-American',
   'Other',
   'Latino/Hispanic American',
   'Black/African American'],
  'race_o': ['European/Caucasian-American',
   'Asian/Pacific Islander/Asian-American',
   'Latino/Hispanic American',
   'Other',
   'Black/African American'],
  'samerace': ['0', '1'],
  'd_importance_same_race': ['[2-5]', '[6-10]', '[0-1]'],
  'd_importance_same_religion': ['[2-5]', '[0-1]', '[6-10]'],
  'field': ['Law',
   'law',
   

In [78]:
data.data = pd.DataFrame(data.data, columns=data.feature_names)
data.target = pd.Series(data.target)

In [79]:
data.data

has_null  wave  gender   age  age_o  d_age  d_d_age  race  race_o  \
0          0.0   1.0     0.0  21.0   27.0    6.0      0.0   0.0     0.0   
1          0.0   1.0     0.0  21.0   22.0    1.0      1.0   0.0     0.0   
2          1.0   1.0     0.0  21.0   22.0    1.0      1.0   0.0     1.0   
3          0.0   1.0     0.0  21.0   23.0    2.0      2.0   0.0     0.0   
4          0.0   1.0     0.0  21.0   24.0    3.0      2.0   0.0     2.0   
...        ...   ...     ...   ...    ...    ...      ...   ...     ...   
8373       1.0  21.0     1.0  25.0   26.0    1.0      1.0   1.0     2.0   
8374       1.0  21.0     1.0  25.0   24.0    1.0      1.0   1.0     3.0   
8375       1.0  21.0     1.0  25.0   29.0    4.0      0.0   1.0     2.0   
8376       1.0  21.0     1.0  25.0   22.0    3.0      2.0   1.0     1.0   
8377       1.0  21.0     1.0  25.0   22.0    3.0      2.0   1.0     1.0   

      samerace  importance_same_race  importance_same_religion  \
0          0.0                   2.0                       4.0   
1          0.0                   2.0                       4.0   
2          1.0                   2.0                       4.0   
3          0.0                   2.0                       4.0   
4          0.0                   2.0                       4.0   
...        ...                   ...                       ...   
8373       0.0                   1.0                       1.0   
8374       0.0                   1.0                       1.0   
8375       0.0                   1.0                       1.0   
8376       0.0                   1.0                       1.0   
8377       0.0                   1.0                       1.0   

      d_importance_same_race  d_importance_same_religion  field  \
0                        0.0                         0.0    0.0   
1                        0.0                         0.0    0.0   
2                        0.0                         0.0    0.0   
3                        0.0                         0.0    0.0   
4                        0.0                         0.0    0.0   
...                      ...                         ...    ...   
8373                     2.0                         1.0  258.0   
8374                     2.0                         1.0  258.0   
8375                     2.0                         1.0  258.0   
8376                     2.0                         1.0  258.0   
8377                     2.0                         1.0  258.0   

      pref_o_attractive  pref_o_sincere  pref_o_intelligence  pref_o_funny  \
0                  35.0            20.0                 20.0          20.0   
1                  60.0             0.0                  0.0          40.0   
2                  19.0            18.0                 19.0          18.0   
3                  30.0             5.0                 15.0          40.0   
4                  30.0            10.0                 20.0          10.0   
...                 ...             ...                  ...           ...   
8373               10.0            10.0                 30.0          20.0   
8374               50.0            20.0                 10.0           5.0   
8375               40.0            10.0                 30.0          10.0   
8376               10.0            25.0                 25.0          10.0   
8377               20.0            20.0                 10.0          15.0   

      pref_o_ambitious  pref_o_shared_interests  d_pref_o_attractive  \
0                  0.0                      5.0                  0.0   
1                  0.0                      0.0                  0.0   
2                 14.0                     12.0                  1.0   
3                  5.0                      5.0                  0.0   
4                 10.0                     20.0                  0.0   
...                ...                      ...                  ...   
8373              10.0                     15.0                  2

In [80]:
data.data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 8378 entries, 0 to 8377
Columns: 120 entries, has_null to met
dtypes: float64(120)
memory usage: 7.7 MB


In [81]:
X, Y = preprocess(data)
with open('dataset/{}.pkl'.format(name), 'wb') as f:
    pickle.dump((X, Y), f)

(8378, 120)
isnull:  (7330, 120)
age                              True
age_o                            True
race                             True
race_o                           True
importance_same_race             True
importance_same_religion         True
field                            True
pref_o_attractive                True
pref_o_sincere                   True
pref_o_intelligence              True
pref_o_funny                     True
pref_o_ambitious                 True
pref_o_shared_interests          True
attractive_o                     True
sinsere_o                        True
intelligence_o                   True
funny_o                          True
ambitous_o                       True
shared_interests_o               True
attractive_important             True
sincere_important                True
intellicence_important           True
funny_important                  True
ambtition_important              True
shared_interests_important       True
attractive       

In [82]:
X

has_null=1  gender=male  d_d_age=[0-1]  d_d_age=[2-3]  d_d_age=[4-6]  \
0              0            0              0              0              1   
1              0            0              1              0              0   
2              1            0              1              0              0   
3              0            0              0              1              0   
4              0            0              0              1              0   
...          ...          ...            ...            ...            ...   
8373           1            1              1              0              0   
8374           1            1              1              0              0   
8375           1            1              0              0              1   
8376           1            1              0              1              0   
8377           1            1              0              1              0   

      d_d_age=[7-37]  race=Asian/Pacific Islander/Asian-American  \
0                  0                                           1   
1                  0                                           1   
2                  0                                           1   
3                  0                                           1   
4                  0                                           1   
...              ...                                         ...   
8373               0                                           0   
8374               0                                           0   
8375               0                                           0   
8376               0                                           0   
8377               0                                           0   

      race=Black/African American  race=European/Caucasian-American  \
0                               0                                 0   
1                               0                                 0   
2                               0                                 0   
3                               0                                 0   
4                               0                                 0   
...                           ...                               ...   
8373                            0                                 1   
8374                            0                                 1   
8375                            0                                 1   
8376                            0                                 1   
8377                            0                                 1   

      race=Latino/Hispanic American  race=Other  \
0                                 0           0   
1                                 0           0   
2                                 0           0   
3                                 0           0   
4                                 0           0   
...                             ...         ...   
8373                              0           0   
8374                              0           0   
8375                              0           0   
8376                              0           0   
8377                              0           0   

      race_o=Asian/Pacific Islander/Asian-American  \
0                                                0   
1                                                0   
2                                                1   
3                                                0   
4                                                0   
...                                            ...   
8373                                             0   
8374                                             0   
8375                                             0   
8376                                             1   
8377                                             1   

      race_o=Black/African American  race_o=European/Caucasian-American  \
0                                 0                           

In [83]:
Y

0       0
1       0
2       1
3       1
4       1
       ..
8373    0
8374    0
8375    0
8376    0
8377    0
Length: 8378, dtype: category
Categories (2, object): ['0', '1']

# Bioresponse

In [84]:
name = 'Bioresponse'

In [85]:
data = datasets.fetch_openml(name=name)

In [86]:
data

{'data': array([[0.        , 0.49700901, 0.1       , ..., 0.        , 0.        ,
         0.        ],
        [0.36666667, 0.60629148, 0.05      , ..., 0.        , 1.        ,
         0.        ],
        [0.0333    , 0.48012427, 0.        , ..., 0.        , 0.        ,
         0.        ],
        ...,
        [0.2       , 0.52056377, 0.        , ..., 0.        , 0.        ,
         0.        ],
        [0.1       , 0.7656462 , 0.        , ..., 0.        , 0.        ,
         0.        ],
        [0.13333333, 0.53395198, 0.        , ..., 0.        , 0.        ,
         0.        ]]),
 'target': array(['1', '1', '1', ..., '0', '1', '0'], dtype=object),
 'frame': None,
 'categories': {},
 'feature_names': ['D1',
  'D2',
  'D3',
  'D4',
  'D5',
  'D6',
  'D7',
  'D8',
  'D9',
  'D10',
  'D11',
  'D12',
  'D13',
  'D14',
  'D15',
  'D16',
  'D17',
  'D18',
  'D19',
  'D20',
  'D21',
  'D22',
  'D23',
  'D24',
  'D25',
  'D26',
  'D27',
  'D28',
  'D29',
  'D30',
  'D31',
  'D32',
 

In [87]:
data.data = pd.DataFrame(data.data, columns=data.feature_names)
data.target = pd.Series(data.target)

In [88]:
data.data

D1        D2    D3   D4        D5        D6        D7        D8  \
0     0.000000  0.497009  0.10  0.0  0.132956  0.678031  0.273166  0.585445   
1     0.366667  0.606291  0.05  0.0  0.111209  0.803455  0.106105  0.411754   
2     0.033300  0.480124  0.00  0.0  0.209791  0.610350  0.356453  0.517720   
3     0.000000  0.538825  0.00  0.5  0.196344  0.724230  0.235606  0.288764   
4     0.100000  0.517794  0.00  0.0  0.494734  0.781422  0.154361  0.303809   
...        ...       ...   ...  ...       ...       ...       ...       ...   
3746  0.033300  0.506409  0.10  0.0  0.209887  0.633426  0.297659  0.376124   
3747  0.133333  0.651023  0.15  0.0  0.151154  0.766505  0.170876  0.404546   
3748  0.200000  0.520564  0.00  0.0  0.179949  0.768785  0.177341  0.471179   
3749  0.100000  0.765646  0.00  0.0  0.536954  0.634936  0.342713  0.447162   
3750  0.133333  0.533952  0.00  0.0  0.347966  0.757971  0.230667  0.272652   

            D9       D10       D11     D12       D13       D14       D15  \
0     0.743663  0.243144  0.187856  0.0000  0.000000  0.069000  0.362012   
1     0.836582  0.106480  0.101382  0.1875  0.193548  0.131001  0.350206   
2     0.679051  0.352308  0.193548  0.1250  0.000000  0.068900  0.574628   
3     0.805110  0.208989  0.000000  0.0000  0.000000  0.145947  0.584688   
4     0.812646  0.125177  0.532258  0.0000  0.000000  0.094900  0.540323   
...        ...       ...       ...     ...       ...       ...       ...   
3746  0.727093  0.308163  0.000000  0.0000  0.000000  0.071800  0.362006   
3747  0.787935  0.192527  0.085200  0.2500  0.064500  0.121309  0.347521   
3748  0.872241  0.122132  0.624027  0.1875  0.064500  0.091700  0.519094   
3749  0.672689  0.372936  0.319355  0.1875  0.000000  0.273901  0.549001   
3750  0.854116  0.140316  0.736973  0.1250  0.000000  0.097900  0.548488   

           D16       D17       D18       D19       D20      D21       D22  \
0     0.301773  0.597930  0.190813  0.107219  0.070500  0.00717  0.137931   
1     0.187419  0.762669  0.180473  0.329962  0.107681  0.01950  0.206897   
2     0.283327  0.510633  0.184480  0.073300  0.061600  0.00566  0.000000   
3     0.325247  0.496745  0.242288  0.087700  0.075300  0.01680  0.000000   
4     0.116775  0.552982  0.167897  0.116140  0.054200  0.01350  0.103448   
...        ...       ...       ...       ...       ...      ...       ...   
3746  0.229374  0.603893  0.129706  0.092400  0.036100  0.00473  0.069000   
3747  0.250846  0.660747  0.221975  0.167944  0.065700  0.00939  0.172414   
3748  0.243037  0.691896  0.215831  0.338637  0.290643  0.04450  0.103448   
3749  0.567326  0.427189  0.332955  0.168837  0.105198  0.02240  0.034500   
3750  0.170359  0.608174  0.198938  0.161527  0.302829  0.02470  0.069000   

      D23   D24       D25       D26  D27  D28       D29       D30       D31  \
0     1.0  0.00  0.496683  0.753131  1.0  1.0  0.000000  0.262919  0.077200   
1     0.0  0.75  0.449869  0.720484  0.0  0.0  0.666667  0.099400  0.289240   
2     1.0  0.00  0.486610  0.803577  0.0  1.0  0.000000  0.428659  0.032400   
3     1.0  0.00  0.459122  0.829482  0.0  1.0  0.000000  0.435410  0.118562   
4     1.0  0.00  0.381883  0.913374  0.0  1.0  0.000000  0.305333  0.054100   
...   ...   ...       ...       ...  ...  ...       ...       ...       ...   
3746  1.0  0.00  0.486439  0.783710  1.0  1.0  0.000000  0.364694  0.136861   
3747  1.0  0.00  0.390864  0.815279  0.0  1.0  0.000000  0.153533  0.127563   
3748  1.0  0.00  0.590995  0.581372  0.0  0.0  0.333333  0.128839  0.357203   
3749  1.0  0.00  0.471154  0.795728  1.0  1.0  0.000000  0.282592  0.005600   
3750  1.0  0.00  0.477220  0.821335  0.0  1.0  0.000000  0.221986  0.217089   

           D32       D33      D34       D35       D36   D37       D38  \
0     0.082700  0.200590  0.00000  0.000000  0.000000  0.00  0.162383   
1     0.216710  0.100295  0.16958  0.235294  0.000000  0.00  0.119104   
2     0.072400  0.000000  0.03930  0.000000  0.000000  0.

In [89]:
data.data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 3751 entries, 0 to 3750
Columns: 1776 entries, D1 to D1776
dtypes: float64(1776)
memory usage: 50.8 MB


In [90]:
X, Y = preprocess(data)
with open('dataset/{}.pkl'.format(name), 'wb') as f:
    pickle.dump((X, Y), f)

(3751, 1776)
isnull:  (0, 1776)
Series([], dtype: bool)
isnull again:  (0, 1776)
Series([], dtype: bool)


/Users/janfan/.pyenv/versions/anaconda3-2020.11/lib/python3.8/site-packages/sklearn/preprocessing/_discretization.py:189: ConvergenceWarning: Number of distinct clusters (4) found smaller than n_clusters (5). Possibly due to duplicate points in X.
  centers = km.fit(column[:, None]).cluster_centers_[:, 0]
/Users/janfan/.pyenv/versions/anaconda3-2020.11/lib/python3.8/site-packages/sklearn/preprocessing/_discretization.py:200: UserWarning: Bins whose width are too small (i.e., <= 1e-8) in feature 218 are removed. Consider decreasing the number of bins.
  warnings.warn('Bins whose width are too small (i.e., <= '
/Users/janfan/.pyenv/versions/anaconda3-2020.11/lib/python3.8/site-packages/sklearn/preprocessing/_discretization.py:189: ConvergenceWarning: Number of distinct clusters (4) found smaller than n_clusters (5). Possibly due to duplicate points in X.
  centers = km.fit(column[:, None]).cluster_centers_[:, 0]
/Users/janfan/.pyenv/versions/anaconda3-2020.11/lib/python3.8/site-packages/

(3751, 5333)


In [91]:
X

D4=0.0  D4=0.25  D4=0.5  D4=0.75  D4=1.0  D23=1.0  D24=0.0  D24=0.25  \
0          1        0       0        0       0        1        1         0   
1          1        0       0        0       0        0        0         0   
2          1        0       0        0       0        1        1         0   
3          0        0       1        0       0        1        1         0   
4          1        0       0        0       0        1        1         0   
...      ...      ...     ...      ...     ...      ...      ...       ...   
3746       1        0       0        0       0        1        1         0   
3747       1        0       0        0       0        1        1         0   
3748       1        0       0        0       0        1        1         0   
3749       1        0       0        0       0        1        1         0   
3750       1        0       0        0       0        1        1         0   

      D24=0.5  D24=0.75  D24=1.0  D27=1.0  D28=1.0  D51=1.0  D72=1.0  D81=0.0  \
0           0         0        0        1        1        0        0        1   
1           0         1        0        0        0        0        0        1   
2           0         0        0        0        1        1        0        1   
3           0         0        0        0        1        0        0        1   
4           0         0        0        0        1        0        0        1   
...       ...       ...      ...      ...      ...      ...      ...      ...   
3746        0         0        0        1        1        0        0        1   
3747        0         0        0        0        1        1        0        1   
3748        0         0        0        0        0        1        0        1   
3749        0         0        0        1        1        1        0        1   
3750        0         0        0        0        1        0        0        1   

      D81=0.333333333  D81=0.666666667  D81=1.0  D82=0.0  D82=0.25  D82=0.5  \
0                   0                0        0        1         0        0   
1                   0                0        0        1         0        0   
2                   0                0        0        1         0        0   
3                   0                0        0        1         0        0   
4                   0                0        0        1         0        0   
...               ...              ...      ...      ...       ...      ...   
3746                0                0        0        1         0        0   
3747                0                0        0        0         1        0   
3748                0                0        0        0         1        0   
3749                0                0        0        1         0        0   
3750                0                0        0        1         0        0   

      D82=0.75  D82=1.0  D94=1.0  D98=0.0  D98=0.2  D98=0.4  D98=0.6  D98=0.8  \
0            0        0        0        1        0        0        0        0   
1            0        0        1        0        0        1        0        0   
2            0        0        0        1        0        0        0        0   
3            0        0        0        1        0        0        0        0   
4            0        0        1        1        0        0        0        0   
...        ...      ...      ...      ...      ...      ...      ...      ...   
3746         0        0        0        1        0        0        0        0   
3747         0        0        1        1        0        0        0        0   
3748         0        0        1        1        0        0        0        0   
3749         0        0        0        1        0        0        0        0   
3750         0        0        0        1        0        0        0        0   

      D112=0.0  D112=0.2  D112=0.4  D112=0.6  D112=0.8  D116=0.0  D116=0.25  \
0            1         0         0         0         0         1          0   
1            1  

In [92]:
Y

0       1
1       1
2       1
3       1
4       0
       ..
3746    1
3747    1
3748    0
3749    1
3750    0
Length: 3751, dtype: category
Categories (2, object): ['0', '1']

# letter

In [93]:
name = 'letter'

In [94]:
data = datasets.fetch_openml(name=name)

/Users/janfan/.pyenv/versions/anaconda3-2020.11/lib/python3.8/site-packages/sklearn/datasets/_openml.py:373: UserWarning: Multiple active versions of the dataset matching the name letter exist. Versions may be fundamentally different, returning version 1.
  warn("Multiple active versions of the dataset matching the name"


In [95]:
data

{'data': array([[ 2.,  4.,  4., ...,  8.,  5.,  6.],
        [ 4.,  7.,  5., ...,  9.,  7., 10.],
        [ 7., 10.,  8., ...,  5.,  5., 10.],
        ...,
        [ 4.,  8.,  4., ...,  9.,  3.,  7.],
        [ 4., 11.,  4., ...,  8.,  0.,  8.],
        [ 5.,  9.,  6., ...,  8.,  6.,  8.]]),
 'target': array(['Z', 'P', 'S', ..., 'O', 'L', 'Q'], dtype=object),
 'frame': None,
 'categories': {},
 'feature_names': ['x-box',
  'y-box',
  'width',
  'high',
  'onpix',
  'x-bar',
  'y-bar',
  'x2bar',
  'y2bar',
  'xybar',
  'x2ybr',
  'xy2br',
  'x-ege',
  'xegvy',
  'y-ege',
  'yegvx'],
 'target_names': ['class'],
 'DESCR': '**Author**: David J. Slate  \n**Source**: [UCI](https://archive.ics.uci.edu/ml/datasets/Letter+Recognition) - 01-01-1991  \n**Please cite**: P. W. Frey and D. J. Slate. "Letter Recognition Using Holland-style Adaptive Classifiers". Machine Learning 6(2), 1991  \n\n1. TITLE: \n  Letter Image Recognition Data \n \n    The objective is to identify each of a large number o

In [96]:
data.data = pd.DataFrame(data.data, columns=data.feature_names)
data.target = pd.Series(data.target)

In [97]:
data.data

x-box  y-box  width  high  onpix  x-bar  y-bar  x2bar  y2bar  xybar  \
0        2.0    4.0    4.0   3.0    2.0    7.0    8.0    2.0    9.0   11.0   
1        4.0    7.0    5.0   5.0    5.0    5.0    9.0    6.0    4.0    8.0   
2        7.0   10.0    8.0   7.0    4.0    8.0    8.0    5.0   10.0   11.0   
3        4.0    9.0    5.0   7.0    4.0    7.0    7.0   13.0    1.0    7.0   
4        6.0    7.0    8.0   5.0    4.0    7.0    6.0    3.0    7.0   10.0   
...      ...    ...    ...   ...    ...    ...    ...    ...    ...    ...   
19995    5.0   10.0    5.0   8.0    3.0    4.0   10.0    7.0    8.0   12.0   
19996    4.0    7.0    6.0   5.0    3.0    7.0    8.0    2.0   10.0   12.0   
19997    4.0    8.0    4.0   6.0    4.0    7.0    8.0    7.0    4.0   10.0   
19998    4.0   11.0    4.0   8.0    3.0    0.0    2.0    4.0    6.0    1.0   
19999    5.0    9.0    6.0  11.0    6.0    8.0    7.0    6.0    3.0    8.0   

       x2ybr  xy2br  x-ege  xegvy  y-ege  yegvx  
0        7.0    7.0    1.0    8.0    5.0    6.0  
1        7.0    9.0    2.0    9.0    7.0   10.0  
2        2.0    8.0    2.0    5.0    5.0   10.0  
3        6.0    8.0    3.0    8.0    0.0    8.0  
4        7.0    9.0    3.0    8.0    3.0    7.0  
...      ...    ...    ...    ...    ...    ...  
19995   10.0    9.0    2.0    9.0    2.0    6.0  
19996    6.0    8.0    1.0    9.0    6.0    8.0  
19997    7.0    6.0    3.0    9.0    3.0    7.0  
19998    0.0    7.0    0.0    8.0    0.0    8.0  
19999    8.0   11.0    3.0    8.0    6.0    8.0  

[20000 rows x 16 columns]

In [98]:
data.data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 20000 entries, 0 to 19999
Data columns (total 16 columns):
 #   Column  Non-Null Count  Dtype  
---  ------  --------------  -----  
 0   x-box   20000 non-null  float64
 1   y-box   20000 non-null  float64
 2   width   20000 non-null  float64
 3   high    20000 non-null  float64
 4   onpix   20000 non-null  float64
 5   x-bar   20000 non-null  float64
 6   y-bar   20000 non-null  float64
 7   x2bar   20000 non-null  float64
 8   y2bar   20000 non-null  float64
 9   xybar   20000 non-null  float64
 10  x2ybr   20000 non-null  float64
 11  xy2br   20000 non-null  float64
 12  x-ege   20000 non-null  float64
 13  xegvy   20000 non-null  float64
 14  y-ege   20000 non-null  float64
 15  yegvx   20000 non-null  float64
dtypes: float64(16)
memory usage: 2.4 MB


In [99]:
X, Y = preprocess(data)
with open('dataset/{}.pkl'.format(name), 'wb') as f:
    pickle.dump((X, Y), f)

(20000, 16)
isnull:  (0, 16)
Series([], dtype: bool)
isnull again:  (0, 16)
Series([], dtype: bool)
(20000, 80)


In [100]:
X

x-box=[0.00-3.52]  x-box=[3.52-6.16]  x-box=[6.16-9.03]  \
0                      1                  0                  0   
1                      0                  1                  0   
2                      0                  0                  1   
3                      0                  1                  0   
4                      0                  1                  0   
...                  ...                ...                ...   
19995                  0                  1                  0   
19996                  0                  1                  0   
19997                  0                  1                  0   
19998                  0                  1                  0   
19999                  0                  1                  0   

       x-box=[9.03-12.12]  x-box=[12.12-15.00]  y-box=[0.00-3.41]  \
0                       0                    0                  0   
1                       0                    0                  0   
2                       0                    0                  0   
3                       0                    0                  0   
4                       0                    0                  0   
...                   ...                  ...                ...   
19995                   0                    0                  0   
19996                   0                    0                  0   
19997                   0                    0                  0   
19998                   0                    0                  0   
19999                   0                    0                  0   

       y-box=[3.41-6.57]  y-box=[6.57-9.30]  y-box=[9.30-12.24]  \
0                      1                  0                   0   
1                      0                  1                   0   
2                      0                  0                   1   
3                      0                  1                   0   
4                      0                  1                   0   
...                  ...                ...                 ...   
19995                  0                  0                   1   
19996                  0                  1                   0   
19997                  0                  1                   0   
19998                  0                  0                   1   
19999                  0                  1                   0   

       y-box=[12.24-15.00]  width=[0.00-3.65]  width=[3.65-6.34]  \
0                        0                  0                  1   
1                        0                  0                  1   
2                        0                  0                  0   
3                        0                  0                  1   
4                        0                  0                  0   
...                    ...                ...                ...   
19995                    0                  0                  1   
19996                    0                  0                  1   
19997                    0                  0                  1   
19998                    0                  0                  1   
19999                    0                  0                  1   

       width=[6.34-9.07]  width=[9.07-12.06]  width=[12.06-15.00]  \
0                      0                   0                    0   
1                      0                   0                    0   
2                      1                   0                    0   
3                      0                   0                    0   
4                      1                   0                    0   
...                  ...                 ...                  ...   
19995                  0                   0                    0   
19996                  0                   0                    0   
19997                  0                   0                    0   
19998                  0                   0                    0   
1999

In [101]:
Y

0        Z
1        P
2        S
3        H
4        H
        ..
19995    C
19996    Z
19997    O
19998    L
19999    Q
Length: 20000, dtype: category
Categories (26, object): ['A', 'B', 'C', 'D', ..., 'W', 'X', 'Y', 'Z']

# PhishingWebsites

In [102]:
name = 'PhishingWebsites'

In [103]:
data = datasets.fetch_openml(name=name)

In [104]:
data

{'data': array([[0., 0., 0., ..., 0., 0., 0.],
        [1., 0., 0., ..., 0., 0., 1.],
        [1., 1., 0., ..., 0., 1., 0.],
        ...,
        [1., 2., 0., ..., 0., 1., 1.],
        [0., 2., 0., ..., 0., 0., 1.],
        [0., 2., 0., ..., 1., 0., 0.]]),
 'target': array(['-1', '-1', '-1', ..., '-1', '-1', '-1'], dtype=object),
 'frame': None,
 'categories': {'having_IP_Address': ['-1', '1'],
  'URL_Length': ['1', '0', '-1'],
  'Shortining_Service': ['1', '-1'],
  'having_At_Symbol': ['1', '-1'],
  'double_slash_redirecting': ['-1', '1'],
  'Prefix_Suffix': ['-1', '1'],
  'having_Sub_Domain': ['-1', '0', '1'],
  'SSLfinal_State': ['-1', '1', '0'],
  'Domain_registeration_length': ['-1', '1'],
  'Favicon': ['1', '-1'],
  'port': ['1', '-1'],
  'HTTPS_token': ['-1', '1'],
  'Request_URL': ['1', '-1'],
  'URL_of_Anchor': ['-1', '0', '1'],
  'Links_in_tags': ['1', '-1', '0'],
  'SFH': ['-1', '1', '0'],
  'Submitting_to_email': ['-1', '1'],
  'Abnormal_URL': ['-1', '1'],
  'Redirect': ['0

In [105]:
data.data = pd.DataFrame(data.data, columns=data.feature_names)
data.target = pd.Series(data.target)

In [106]:
data.data

having_IP_Address  URL_Length  Shortining_Service  having_At_Symbol  \
0                    0.0         0.0                 0.0               0.0   
1                    1.0         0.0                 0.0               0.0   
2                    1.0         1.0                 0.0               0.0   
3                    1.0         1.0                 0.0               0.0   
4                    1.0         1.0                 1.0               0.0   
...                  ...         ...                 ...               ...   
11050                1.0         2.0                 0.0               1.0   
11051                0.0         0.0                 0.0               1.0   
11052                1.0         2.0                 0.0               0.0   
11053                0.0         2.0                 0.0               0.0   
11054                0.0         2.0                 0.0               0.0   

       double_slash_redirecting  Prefix_Suffix  having_Sub_Domain  \
0                           0.0            0.0                0.0   
1                           1.0            0.0                1.0   
2                           1.0            0.0                0.0   
3                           1.0            0.0                0.0   
4                           1.0            0.0                2.0   
...                         ...            ...                ...   
11050                       1.0            1.0                2.0   
11051                       0.0            0.0                2.0   
11052                       1.0            0.0                2.0   
11053                       1.0            0.0                0.0   
11054                       1.0            0.0                0.0   

       SSLfinal_State  Domain_registeration_length  Favicon  port  \
0                 0.0                          0.0      0.0   0.0   
1                 1.0                          0.0      0.0   0.0   
2                 0.0                          0.0      0.0   0.0   
3                 0.0                          1.0      0.0   0.0   
4                 1.0                          0.0      0.0   0.0   
...               ...                          ...      ...   ...   
11050             1.0                          0.0      1.0   1.0   
11051             0.0                          0.0      1.0   1.0   
11052             0.0                          0.0      0.0   0.0   
11053             0.0                          1.0      1.0   0.0   
11054             0.0                          1.0      0.0   0.0   

       HTTPS_token  Request_URL  URL_of_Anchor  Links_in_tags  SFH  \
0              0.0          0.0            0.0            0.0  0.0   
1              0.0          0.0            1.0            1.0  0.0   
2              0.0          0.0            1.0            1.0  0.0   
3              0.0          1.0            1.0            2.0  0.0   
4              1.0          0.0            1.0            2.0  0.0   
...            ...          ...            ...            ...  ...   
11050          1.0          0.0            2.0            0.0  0.0   
11051          1.0          0.0            0.0            1.0  2.0   
11052          1.0          0.0            1.0            1.0  0.0   
11053          1.0          1.0            0.0            0.0  0.0   
11054          1.0          1.0            0.0            2.0  0.0   

       Submitting_to_email  Abnormal_URL  Redirect  on_mouseover  RightClick  \
0                      0.0           0.0       0.0           0.0         0.0   
1                      1.0           1.0       0.0           0.0         0.0   
2                      0.0           0.0       0.0           0.0         0.0   
3                      1.0           1.0       0.0           0.0         0.0   
4                      1.0           1.0       0.0           1.0         0.0   
...                    ...           ...       ...           ...         ...   
11050      

In [107]:
data.data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 11055 entries, 0 to 11054
Data columns (total 30 columns):
 #   Column                       Non-Null Count  Dtype  
---  ------                       --------------  -----  
 0   having_IP_Address            11055 non-null  float64
 1   URL_Length                   11055 non-null  float64
 2   Shortining_Service           11055 non-null  float64
 3   having_At_Symbol             11055 non-null  float64
 4   double_slash_redirecting     11055 non-null  float64
 5   Prefix_Suffix                11055 non-null  float64
 6   having_Sub_Domain            11055 non-null  float64
 7   SSLfinal_State               11055 non-null  float64
 8   Domain_registeration_length  11055 non-null  float64
 9   Favicon                      11055 non-null  float64
 10  port                         11055 non-null  float64
 11  HTTPS_token                  11055 non-null  float64
 12  Request_URL                  11055 non-null  float64
 13  URL_of_Anchor   

In [108]:
X, Y = preprocess(data)
with open('dataset/{}.pkl'.format(name), 'wb') as f:
    pickle.dump((X, Y), f)

(11055, 30)
isnull:  (0, 30)
Series([], dtype: bool)
isnull again:  (0, 30)
Series([], dtype: bool)
(11055, 46)


In [109]:
X

having_IP_Address=1  URL_Length=-1  URL_Length=0  URL_Length=1  \
0                        0              0             0             1   
1                        1              0             0             1   
2                        1              0             1             0   
3                        1              0             1             0   
4                        1              0             1             0   
...                    ...            ...           ...           ...   
11050                    1              1             0             0   
11051                    0              0             0             1   
11052                    1              1             0             0   
11053                    0              1             0             0   
11054                    0              1             0             0   

       Shortining_Service=1  having_At_Symbol=1  double_slash_redirecting=1  \
0                         1                   1                           0   
1                         1                   1                           1   
2                         1                   1                           1   
3                         1                   1                           1   
4                         0                   1                           1   
...                     ...                 ...                         ...   
11050                     1                   0                           1   
11051                     1                   0                           0   
11052                     1                   1                           1   
11053                     1                   1                           1   
11054                     1                   1                           1   

       Prefix_Suffix=1  having_Sub_Domain=-1  having_Sub_Domain=0  \
0                    0                     1                    0   
1                    0                     0                    1   
2                    0                     1                    0   
3                    0                     1                    0   
4                    0                     0                    0   
...                ...                   ...                  ...   
11050                1                     0                    0   
11051                0                     0                    0   
11052                0                     0                    0   
11053                0                     1                    0   
11054                0                     1                    0   

       having_Sub_Domain=1  SSLfinal_State=-1  SSLfinal_State=0  \
0                        0                  1                 0   
1                        0                  0                 0   
2                        0                  1                 0   
3                        0                  1                 0   
4                        1                  0                 0   
...                    ...                ...               ...   
11050                    1                  0                 0   
11051                    1                  1                 0   
11052                    1                  1                 0   
11053                    0                  1                 0   
11054                    0                  1                 0   

       SSLfinal_State=1  Domain_registeration_length=1  Favicon=1  port=1  \
0                     0                              0          1       1   
1                     1                              0          1       1   
2                     0                              0          1       1   
3                     0                              1          1       1   
4                     1                              0          1       1   
...                 ...                            ...        ...     ...   
11050   

In [110]:
Y

0        -1
1        -1
2        -1
3        -1
4         1
         ..
11050     1
11051    -1
11052    -1
11053    -1
11054    -1
Length: 11055, dtype: category
Categories (2, object): ['-1', '1']

# electricity

In [111]:
name = 'electricity'

In [112]:
data = datasets.fetch_openml(name=name)

In [113]:
data

{'data': array([[0.00000e+00, 1.00000e+00, 0.00000e+00, ..., 3.46700e-03,
         4.22915e-01, 4.14912e-01],
        [0.00000e+00, 1.00000e+00, 2.12770e-02, ..., 3.46700e-03,
         4.22915e-01, 4.14912e-01],
        [0.00000e+00, 1.00000e+00, 4.25530e-02, ..., 3.46700e-03,
         4.22915e-01, 4.14912e-01],
        ...,
        [9.15800e-01, 6.00000e+00, 9.57447e-01, ..., 2.98300e-03,
         2.47799e-01, 3.62281e-01],
        [9.15800e-01, 6.00000e+00, 9.78723e-01, ..., 4.63000e-03,
         3.45417e-01, 2.06579e-01],
        [9.15800e-01, 6.00000e+00, 1.00000e+00, ..., 3.54200e-03,
         3.55256e-01, 2.31140e-01]]),
 'target': array(['UP', 'UP', 'UP', ..., 'DOWN', 'UP', 'DOWN'], dtype=object),
 'frame': None,
 'categories': {'day': ['1', '2', '3', '4', '5', '6', '7']},
 'feature_names': ['date',
  'day',
  'period',
  'nswprice',
  'nswdemand',
  'vicprice',
  'vicdemand',
  'transfer'],
 'target_names': ['class'],
 'DESCR': '**Author**: M. Harries, J. Gama, A. Bifet  \n**So

In [114]:
data.data = pd.DataFrame(data.data, columns=data.feature_names)
data.target = pd.Series(data.target)

In [115]:
data.data

date  day    period  nswprice  nswdemand  vicprice  vicdemand  \
0      0.0000  1.0  0.000000  0.056443   0.439155  0.003467   0.422915   
1      0.0000  1.0  0.021277  0.051699   0.415055  0.003467   0.422915   
2      0.0000  1.0  0.042553  0.051489   0.385004  0.003467   0.422915   
3      0.0000  1.0  0.063830  0.045485   0.314639  0.003467   0.422915   
4      0.0000  1.0  0.085106  0.042482   0.251116  0.003467   0.422915   
...       ...  ...       ...       ...        ...       ...        ...   
45307  0.9158  6.0  0.914894  0.044224   0.340672  0.003033   0.255049   
45308  0.9158  6.0  0.936170  0.044884   0.355549  0.003072   0.241326   
45309  0.9158  6.0  0.957447  0.043593   0.340970  0.002983   0.247799   
45310  0.9158  6.0  0.978723  0.066651   0.329366  0.004630   0.345417   
45311  0.9158  6.0  1.000000  0.050679   0.288753  0.003542   0.355256   

       transfer  
0      0.414912  
1      0.414912  
2      0.414912  
3      0.414912  
4      0.414912  
...         ...  
45307  0.405263  
45308  0.420614  
45309  0.362281  
45310  0.206579  
45311  0.231140  

[45312 rows x 8 columns]

In [116]:
data.data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 45312 entries, 0 to 45311
Data columns (total 8 columns):
 #   Column     Non-Null Count  Dtype  
---  ------     --------------  -----  
 0   date       45312 non-null  float64
 1   day        45312 non-null  float64
 2   period     45312 non-null  float64
 3   nswprice   45312 non-null  float64
 4   nswdemand  45312 non-null  float64
 5   vicprice   45312 non-null  float64
 6   vicdemand  45312 non-null  float64
 7   transfer   45312 non-null  float64
dtypes: float64(8)
memory usage: 2.8 MB


In [117]:
X, Y = preprocess(data)
with open('dataset/{}.pkl'.format(name), 'wb') as f:
    pickle.dump((X, Y), f)

(45312, 8)
isnull:  (0, 8)
Series([], dtype: bool)
isnull again:  (0, 8)
Series([], dtype: bool)
(45312, 42)


In [118]:
X

day=1  day=2  day=3  day=4  day=5  day=6  day=7  date=[0.00-0.01]  \
0          0      1      0      0      0      0      0                 1   
1          0      1      0      0      0      0      0                 1   
2          0      1      0      0      0      0      0                 1   
3          0      1      0      0      0      0      0                 1   
4          0      1      0      0      0      0      0                 1   
...      ...    ...    ...    ...    ...    ...    ...               ...   
45307      0      0      0      0      0      0      1                 0   
45308      0      0      0      0      0      0      1                 0   
45309      0      0      0      0      0      0      1                 0   
45310      0      0      0      0      0      0      1                 0   
45311      0      0      0      0      0      0      1                 0   

       date=[0.01-0.24]  date=[0.24-0.67]  date=[0.67-0.94]  date=[0.94-1.00]  \
0                     0                 0                 0                 0   
1                     0                 0                 0                 0   
2                     0                 0                 0                 0   
3                     0                 0                 0                 0   
4                     0                 0                 0                 0   
...                 ...               ...               ...               ...   
45307                 0                 0                 1                 0   
45308                 0                 0                 1                 0   
45309                 0                 0                 1                 0   
45310                 0                 0                 1                 0   
45311                 0                 0                 1                 0   

       period=[0.00-0.20]  period=[0.20-0.40]  period=[0.40-0.60]  \
0                       1                   0                   0   
1                       1                   0                   0   
2                       1                   0                   0   
3                       1                   0                   0   
4                       1                   0                   0   
...                   ...                 ...                 ...   
45307                   0                   0                   0   
45308                   0                   0                   0   
45309                   0                   0                   0   
45310                   0                   0                   0   
45311                   0                   0                   0   

       period=[0.60-0.80]  period=[0.80-1.00]  nswprice=[0.00-0.06]  \
0                       0                   0                     1   
1                       0                   0                     1   
2                       0                   0                     1   
3                       0                   0                     1   
4                       0                   0                     1   
...                   ...                 ...                   ...   
45307                   0                   1                     1   
45308                   0                   1                     1   
45309                   0                   1                     1   
45310                   0                   1                     0   
45311                   0                   1                     1   

       nswprice=[0.06-0.10]  nswprice=[0.10-0.22]  nswprice=[0.22-0.55]  \
0                         0                     0                     0   
1                         0                     0                     0   
2                         0                     0                     0   
3                         0                     0                     0   
4                         0                     0               

In [119]:
Y

0          UP
1          UP
2          UP
3          UP
4        DOWN
         ... 
45307    DOWN
45308    DOWN
45309    DOWN
45310      UP
45311    DOWN
Length: 45312, dtype: category
Categories (2, object): ['DOWN', 'UP']

# bank-marketing

In [120]:
name = 'bank-marketing'

In [121]:
data = datasets.fetch_openml(name=name)

/Users/janfan/.pyenv/versions/anaconda3-2020.11/lib/python3.8/site-packages/sklearn/datasets/_openml.py:373: UserWarning: Multiple active versions of the dataset matching the name bank-marketing exist. Versions may be fundamentally different, returning version 1.
  warn("Multiple active versions of the dataset matching the name"


In [122]:
data

{'data': array([[ 58.,   4.,   1., ...,  -1.,   0.,   3.],
        [ 44.,   9.,   2., ...,  -1.,   0.,   3.],
        [ 33.,   2.,   1., ...,  -1.,   0.,   3.],
        ...,
        [ 72.,   5.,   1., ..., 184.,   3.,   2.],
        [ 57.,   1.,   1., ...,  -1.,   0.,   3.],
        [ 37.,   2.,   1., ..., 188.,  11.,   1.]]),
 'target': array(['1', '1', '1', ..., '2', '1', '1'], dtype=object),
 'frame': None,
 'categories': {'V2': ['admin.',
   'blue-collar',
   'entrepreneur',
   'housemaid',
   'management',
   'retired',
   'self-employed',
   'services',
   'student',
   'technician',
   'unemployed',
   'unknown'],
  'V3': ['divorced', 'married', 'single'],
  'V4': ['primary', 'secondary', 'tertiary', 'unknown'],
  'V5': ['no', 'yes'],
  'V7': ['no', 'yes'],
  'V8': ['no', 'yes'],
  'V9': ['cellular', 'telephone', 'unknown'],
  'V11': ['apr',
   'aug',
   'dec',
   'feb',
   'jan',
   'jul',
   'jun',
   'mar',
   'may',
   'nov',
   'oct',
   'sep'],
  'V16': ['failure', 'other'

In [123]:
data.data = pd.DataFrame(data.data, columns=data.feature_names)
data.target = pd.Series(data.target)

In [124]:
data.data

V1    V2   V3   V4   V5      V6   V7   V8   V9   V10  V11     V12  \
0      58.0   4.0  1.0  2.0  0.0  2143.0  1.0  0.0  2.0   5.0  8.0   261.0   
1      44.0   9.0  2.0  1.0  0.0    29.0  1.0  0.0  2.0   5.0  8.0   151.0   
2      33.0   2.0  1.0  1.0  0.0     2.0  1.0  1.0  2.0   5.0  8.0    76.0   
3      47.0   1.0  1.0  3.0  0.0  1506.0  1.0  0.0  2.0   5.0  8.0    92.0   
4      33.0  11.0  2.0  3.0  0.0     1.0  0.0  0.0  2.0   5.0  8.0   198.0   
...     ...   ...  ...  ...  ...     ...  ...  ...  ...   ...  ...     ...   
45206  51.0   9.0  1.0  2.0  0.0   825.0  0.0  0.0  0.0  17.0  9.0   977.0   
45207  71.0   5.0  0.0  0.0  0.0  1729.0  0.0  0.0  0.0  17.0  9.0   456.0   
45208  72.0   5.0  1.0  1.0  0.0  5715.0  0.0  0.0  0.0  17.0  9.0  1127.0   
45209  57.0   1.0  1.0  1.0  0.0   668.0  0.0  0.0  1.0  17.0  9.0   508.0   
45210  37.0   2.0  1.0  1.0  0.0  2971.0  0.0  0.0  0.0  17.0  9.0   361.0   

       V13    V14   V15  V16  
0      1.0   -1.0   0.0  3.0  
1      1.0   -1.0   0.0  3.0  
2      1.0   -1.0   0.0  3.0  
3      1.0   -1.0   0.0  3.0  
4      1.0   -1.0   0.0  3.0  
...    ...    ...   ...  ...  
45206  3.0   -1.0   0.0  3.0  
45207  2.0   -1.0   0.0  3.0  
45208  5.0  184.0   3.0  2.0  
45209  4.0   -1.0   0.0  3.0  
45210  2.0  188.0  11.0  1.0  

[45211 rows x 16 columns]

In [125]:
data.data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 45211 entries, 0 to 45210
Data columns (total 16 columns):
 #   Column  Non-Null Count  Dtype  
---  ------  --------------  -----  
 0   V1      45211 non-null  float64
 1   V2      45211 non-null  float64
 2   V3      45211 non-null  float64
 3   V4      45211 non-null  float64
 4   V5      45211 non-null  float64
 5   V6      45211 non-null  float64
 6   V7      45211 non-null  float64
 7   V8      45211 non-null  float64
 8   V9      45211 non-null  float64
 9   V10     45211 non-null  float64
 10  V11     45211 non-null  float64
 11  V12     45211 non-null  float64
 12  V13     45211 non-null  float64
 13  V14     45211 non-null  float64
 14  V15     45211 non-null  float64
 15  V16     45211 non-null  float64
dtypes: float64(16)
memory usage: 5.5 MB


In [126]:
X, Y = preprocess(data)
with open('dataset/{}.pkl'.format(name), 'wb') as f:
    pickle.dump((X, Y), f)

(45211, 16)
isnull:  (0, 16)
Series([], dtype: bool)
isnull again:  (0, 16)
Series([], dtype: bool)
(45211, 76)


In [127]:
X

V2=admin.  V2=blue-collar  V2=entrepreneur  V2=housemaid  \
0              0               0                0             0   
1              0               0                0             0   
2              0               0                1             0   
3              0               1                0             0   
4              0               0                0             0   
...          ...             ...              ...           ...   
45206          0               0                0             0   
45207          0               0                0             0   
45208          0               0                0             0   
45209          0               1                0             0   
45210          0               0                1             0   

       V2=management  V2=retired  V2=self-employed  V2=services  V2=student  \
0                  1           0                 0            0           0   
1                  0           0                 0            0           0   
2                  0           0                 0            0           0   
3                  0           0                 0            0           0   
4                  0           0                 0            0           0   
...              ...         ...               ...          ...         ...   
45206              0           0                 0            0           0   
45207              0           1                 0            0           0   
45208              0           1                 0            0           0   
45209              0           0                 0            0           0   
45210              0           0                 0            0           0   

       V2=technician  V2=unemployed  V2=unknown  V3=divorced  V3=married  \
0                  0              0           0            0           1   
1                  1              0           0            0           0   
2                  0              0           0            0           1   
3                  0              0           0            0           1   
4                  0              0           1            0           0   
...              ...            ...         ...          ...         ...   
45206              1              0           0            0           1   
45207              0              0           0            1           0   
45208              0              0           0            0           1   
45209              0              0           0            0           1   
45210              0              0           0            0           1   

       V3=single  V4=primary  V4=secondary  V4=tertiary  V4=unknown  V5=yes  \
0              0           0             0            1           0       0   
1              1           0             1            0           0       0   
2              0           0             1            0           0       0   
3              0           0             0            0           1       0   
4              1           0             0            0           1       0   
...          ...         ...           ...          ...         ...     ...   
45206          0           0             0            1           0       0   
45207          0           1             0            0           0       0   
45208          0           0             1            0           0       0   
45209          0           0             1            0           0       0   
45210          0           0             1            0           0       0   

       V7=yes  V8=yes  V9=cellular  V9=telephone  V9=unknown  V11=apr  \
0           1       0            0             0           1        0   
1           1       0            0             0           1        0   
2           1       1            0             0           1        0   
3           1       0            0             0           1        0   
4           0       0     

In [128]:
Y

0        1
1        1
2        1
3        1
4        1
        ..
45206    2
45207    2
45208    2
45209    1
45210    1
Length: 45211, dtype: category
Categories (2, object): ['1', '2']

# Non-openml

## diabetic

In [129]:
name = 'diabetic'

In [130]:
# https://www.hindawi.com/journals/bmri/2014/781670/tab1/
# http://downloads.hindawi.com/journals/bmri/2014/781670.pdf
data = pd.read_csv('dataset/diabetic.csv', sep=",", header=0, engine='python', na_values=['?'])

In [131]:
data.head()

encounter_id  patient_nbr             race  gender      age weight  \
0       2278392      8222157        Caucasian  Female   [0-10)    NaN   
1        149190     55629189        Caucasian  Female  [10-20)    NaN   
2         64410     86047875  AfricanAmerican  Female  [20-30)    NaN   
3        500364     82442376        Caucasian    Male  [30-40)    NaN   
4         16680     42519267        Caucasian    Male  [40-50)    NaN   

   admission_type_id  discharge_disposition_id  admission_source_id  \
0                  6                        25                    1   
1                  1                         1                    7   
2                  1                         1                    7   
3                  1                         1                    7   
4                  1                         1                    7   

   time_in_hospital payer_code         medical_specialty  num_lab_procedures  \
0                 1        NaN  Pediatrics-Endocrinology                  41   
1                 3        NaN                       NaN                  59   
2                 2        NaN                       NaN                  11   
3                 2        NaN                       NaN                  44   
4                 1        NaN                       NaN                  51   

   num_procedures  num_medications  number_outpatient  number_emergency  \
0               0                1                  0                 0   
1               0               18                  0                 0   
2               5               13                  2                 0   
3               1               16                  0                 0   
4               0                8                  0                 0   

   number_inpatient  diag_1  diag_2 diag_3  number_diagnoses max_glu_serum  \
0                 0  250.83     NaN    NaN                 1          None   
1                 0     276  250.01    255                 9          None   
2                 1     648     250    V27                 6          None   
3                 0       8  250.43    403                 7          None   
4                 0     197     157    250                 5          None   

  A1Cresult metformin repaglinide nateglinide chlorpropamide glimepiride  \
0      None        No          No          No             No          No   
1      None        No          No          No             No          No   
2      None        No          No          No             No          No   
3      None        No          No          No             No          No   
4      None        No          No          No             No          No   

  acetohexamide glipizide glyburide tolbutamide pioglitazone rosiglitazone  \
0            No        No        No          No           No            No   
1            No        No        No          No           No            No   
2            No    Steady        No          No           No            No   
3            No        No        No          No           No            No   
4            No    Steady        No          No           No            No   

  acarbose miglitol troglitazone tolazamide examide citoglipton insulin  \
0       No       No           No         No      No          No      No   
1       No       No           No         No      No          No      Up   
2       No       No           No         No      No          No      No   
3       No       No           No         No      No          No      Up   
4       No       No           No         No      No          No  Steady   

  glyburide-metformin glipizide-metformin glimepiride-pioglitazone  \
0                  No                  No                       No   
1                  No                  No                       No   
2                  No                  No                       No   
3                  No                  No                       No   
4        

In [132]:
data.shape

(101766, 50)

In [133]:
print("isnull: ", data[data.isnull().any(axis=1)].shape)
print(data.isnull().any(axis=0)[data.isnull().any(axis=0)])

isnull:  (100723, 50)
race                 True
weight               True
payer_code           True
medical_specialty    True
diag_1               True
diag_2               True
diag_3               True
dtype: bool


In [134]:
Y = data['readmitted']
X = data.drop(columns = ['readmitted', 'encounter_id','patient_nbr','payer_code','diag_1','diag_2','diag_3'])

In [135]:
for c in X.select_dtypes('object').columns:
    X[c] = X[c].astype('category')

In [136]:
print([len(X[c].cat.categories) for c in X.select_dtypes('category').columns])

[5, 3, 10, 9, 72, 4, 4, 4, 4, 4, 4, 4, 2, 4, 4, 2, 4, 4, 4, 4, 2, 3, 1, 1, 4, 4, 2, 2, 2, 2, 2, 2]


In [137]:
X.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 101766 entries, 0 to 101765
Data columns (total 43 columns):
 #   Column                    Non-Null Count   Dtype   
---  ------                    --------------   -----   
 0   race                      99493 non-null   category
 1   gender                    101766 non-null  category
 2   age                       101766 non-null  category
 3   weight                    3197 non-null    category
 4   admission_type_id         101766 non-null  int64   
 5   discharge_disposition_id  101766 non-null  int64   
 6   admission_source_id       101766 non-null  int64   
 7   time_in_hospital          101766 non-null  int64   
 8   medical_specialty         51817 non-null   category
 9   num_lab_procedures        101766 non-null  int64   
 10  num_procedures            101766 non-null  int64   
 11  num_medications           101766 non-null  int64   
 12  number_outpatient         101766 non-null  int64   
 13  number_emergency          101

In [138]:
print({(c, X[c].unique().shape[0]) for c in X.select_dtypes(exclude='category').columns})

{('num_lab_procedures', 118), ('number_emergency', 33), ('discharge_disposition_id', 26), ('number_inpatient', 21), ('admission_type_id', 8), ('number_diagnoses', 16), ('time_in_hospital', 14), ('num_medications', 75), ('admission_source_id', 17), ('number_outpatient', 39), ('num_procedures', 7)}


In [139]:
cols_to_real = ['number_emergency','number_diagnoses','number_inpatient','time_in_hospital',
                'num_lab_procedures','number_outpatient','num_procedures','num_medications']
cols_to_cat = {*X.select_dtypes(exclude='category').columns.tolist()} - set(cols_to_real)

for c in cols_to_real:
    X[c] = X[c].astype(float)
for c in [*cols_to_cat]:
    X[c] = X[c].astype('category')

In [140]:
data = Bunch(data=X, target=Y)
X, Y = preprocess(data)
with open('dataset/{}.pkl'.format(name), 'wb') as f:
    pickle.dump((X, Y), f)

(101766, 43)
isnull:  (100197, 43)
race                 True
weight               True
medical_specialty    True
dtype: bool
isnull again:  (0, 43)
Series([], dtype: bool)
0         No
1         No
2         No
3         No
4         No
          ..
101761    No
101762    No
101763    No
101764    No
101765    No
Name: examide, Length: 101766, dtype: category
Categories (1, object): ['No']
0         No
1         No
2         No
3         No
4         No
          ..
101761    No
101762    No
101763    No
101764    No
101765    No
Name: citoglipton, Length: 101766, dtype: category
Categories (1, object): ['No']
(101766, 264)


In [141]:
X

race=AfricanAmerican  race=Asian  race=Caucasian  race=Hispanic  \
0                          0           0               1              0   
1                          0           0               1              0   
2                          1           0               0              0   
3                          0           0               1              0   
4                          0           0               1              0   
...                      ...         ...             ...            ...   
101761                     1           0               0              0   
101762                     1           0               0              0   
101763                     0           0               1              0   
101764                     0           0               1              0   
101765                     0           0               1              0   

        race=Other  gender=Female  gender=Male  gender=Unknown/Invalid  \
0                0              1            0                       0   
1                0              1            0                       0   
2                0              1            0                       0   
3                0              0            1                       0   
4                0              0            1                       0   
...            ...            ...          ...                     ...   
101761           0              0            1                       0   
101762           0              1            0                       0   
101763           0              0            1                       0   
101764           0              1            0                       0   
101765           0              0            1                       0   

        age=[0-10)  age=[10-20)  age=[20-30)  age=[30-40)  age=[40-50)  \
0                1            0            0            0            0   
1                0            1            0            0            0   
2                0            0            1            0            0   
3                0            0            0            1            0   
4                0            0            0            0            1   
...            ...          ...          ...          ...          ...   
101761           0            0            0            0            0   
101762           0            0            0            0            0   
101763           0            0            0            0            0   
101764           0            0            0            0            0   
101765           0            0            0            0            0   

        age=[50-60)  age=[60-70)  age=[70-80)  age=[80-90)  age=[90-100)  \
0                 0            0            0            0             0   
1                 0            0            0            0             0   
2                 0            0            0            0             0   
3                 0            0            0            0             0   
4                 0            0            0            0             0   
...             ...          ...          ...          ...           ...   
101761            0            0            1            0             0   
101762            0            0            0            1             0   
101763            0            0            1            0             0   
101764            0            0            0            1             0   
101765            0            0            1            0             0   

        weight=>200  weight=[0-25)  weight=[100-125)  weight=[125-150)  \
0                 0              0                 0                 0   
1                 0              0                 0                 0   
2                 0              0                 0                 0   
3                 0              0                 0                 0   
4                 0              0            

In [142]:
Y

0          NO
1         >30
2          NO
3          NO
4          NO
         ... 
101761    >30
101762     NO
101763     NO
101764     NO
101765     NO
Name: readmitted, Length: 101766, dtype: category
Categories (3, object): ['<30', '>30', 'NO']

## shoppers

In [143]:
name = 'shoppers'

In [144]:
data = pd.read_csv('dataset/online_shoppers_intention.csv', sep=",", header=0, engine='python', na_values=['?'])

In [145]:
data.head()

Administrative  Administrative_Duration  Informational  \
0               0                      0.0              0   
1               0                      0.0              0   
2               0                      0.0              0   
3               0                      0.0              0   
4               0                      0.0              0   

   Informational_Duration  ProductRelated  ProductRelated_Duration  \
0                     0.0               1                 0.000000   
1                     0.0               2                64.000000   
2                     0.0               1                 0.000000   
3                     0.0               2                 2.666667   
4                     0.0              10               627.500000   

   BounceRates  ExitRates  PageValues  SpecialDay Month  OperatingSystems  \
0         0.20       0.20         0.0         0.0   Feb                 1   
1         0.00       0.10         0.0         0.0   Feb                 2   
2         0.20       0.20         0.0         0.0   Feb                 4   
3         0.05       0.14         0.0         0.0   Feb                 3   
4         0.02       0.05         0.0         0.0   Feb                 3   

   Browser  Region  TrafficType        VisitorType  Weekend  Revenue  
0        1       1            1  Returning_Visitor    False    False  
1        2       1            2  Returning_Visitor    False    False  
2        1       9            3  Returning_Visitor    False    False  
3        2       2            4  Returning_Visitor    False    False  
4        3       1            4  Returning_Visitor     True    False

In [146]:
data.shape

(12330, 18)

In [147]:
print("isnull: ", data[data.isnull().any(axis=1)].shape)
print(data.isnull().any(axis=0)[data.isnull().any(axis=0)])

isnull:  (0, 18)
Series([], dtype: bool)


In [148]:
Y = data['Revenue']
X = data.drop(columns = ['Revenue'])

In [149]:
for c in ['Month', 'OperatingSystems', 'Browser', 'Region', 'TrafficType', 'VisitorType', 'Weekend',
         'Administrative', 'Informational', 'ProductRelated']: # diff types of sites
    X[c] = X[c].astype('category')

In [150]:
print([len(X[c].cat.categories) for c in X.select_dtypes('category').columns])

[27, 17, 311, 10, 8, 13, 9, 20, 3, 2]


In [151]:
X.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 12330 entries, 0 to 12329
Data columns (total 17 columns):
 #   Column                   Non-Null Count  Dtype   
---  ------                   --------------  -----   
 0   Administrative           12330 non-null  category
 1   Administrative_Duration  12330 non-null  float64 
 2   Informational            12330 non-null  category
 3   Informational_Duration   12330 non-null  float64 
 4   ProductRelated           12330 non-null  category
 5   ProductRelated_Duration  12330 non-null  float64 
 6   BounceRates              12330 non-null  float64 
 7   ExitRates                12330 non-null  float64 
 8   PageValues               12330 non-null  float64 
 9   SpecialDay               12330 non-null  float64 
 10  Month                    12330 non-null  category
 11  OperatingSystems         12330 non-null  category
 12  Browser                  12330 non-null  category
 13  Region                   12330 non-null  category
 14  Traffi

In [152]:
print({(c, X[c].unique().shape[0]) for c in X.select_dtypes(exclude='category').columns})

{('ProductRelated_Duration', 9551), ('PageValues', 2704), ('Administrative_Duration', 3335), ('ExitRates', 4777), ('Informational_Duration', 1258), ('BounceRates', 1872), ('SpecialDay', 6)}


In [153]:
data = Bunch(data=X, target=Y)
X, Y = preprocess(data)
with open('dataset/{}.pkl'.format(name), 'wb') as f:
    pickle.dump((X, Y), f)

(12330, 17)
isnull:  (0, 17)
Series([], dtype: bool)
isnull again:  (0, 17)
Series([], dtype: bool)
(12330, 454)


In [154]:
X

Administrative=0  Administrative=1  Administrative=2  Administrative=3  \
0                     1                 0                 0                 0   
1                     1                 0                 0                 0   
2                     1                 0                 0                 0   
3                     1                 0                 0                 0   
4                     1                 0                 0                 0   
...                 ...               ...               ...               ...   
12325                 0                 0                 0                 1   
12326                 1                 0                 0                 0   
12327                 1                 0                 0                 0   
12328                 0                 0                 0                 0   
12329                 1                 0                 0                 0   

       Administrative=4  Administrative=5  Administrative=6  Administrative=7  \
0                     0                 0                 0                 0   
1                     0                 0                 0                 0   
2                     0                 0                 0                 0   
3                     0                 0                 0                 0   
4                     0                 0                 0                 0   
...                 ...               ...               ...               ...   
12325                 0                 0                 0                 0   
12326                 0                 0                 0                 0   
12327                 0                 0                 0                 0   
12328                 1                 0                 0                 0   
12329                 0                 0                 0                 0   

       Administrative=8  Administrative=9  Administrative=10  \
0                     0                 0                  0   
1                     0                 0                  0   
2                     0                 0                  0   
3                     0                 0                  0   
4                     0                 0                  0   
...                 ...               ...                ...   
12325                 0                 0                  0   
12326                 0                 0                  0   
12327                 0                 0                  0   
12328                 0                 0                  0   
12329                 0                 0                  0   

       Administrative=11  Administrative=12  Administrative=13  \
0                      0                  0                  0   
1                      0                  0                  0   
2                      0                  0                  0   
3                      0                  0                  0   
4                      0                  0                  0   
...                  ...                ...                ...   
12325                  0                  0                  0   
12326                  0                  0                  0   
12327                  0                  0                  0   
12328                  0                  0                  0   
12329                  0                  0                  0   

       Administrative=14  Administrative=15  Administrative=16  \
0                      0                  0                  0   
1                      0                  0                  0   
2                      0                  0                  0   
3                      0                  0                  0   
4                      0                  0                  0   
...                  ...                ...                ...   
12325                  0             

In [155]:
Y

0        False
1        False
2        False
3        False
4        False
         ...  
12325    False
12326    False
12327    False
12328    False
12329    False
Name: Revenue, Length: 12330, dtype: category
Categories (2, object): [False, True]

## default

In [156]:
name = 'default'

In [157]:
data = pd.read_excel('dataset/default of credit card clients.xls', skiprows=1)

In [158]:
data.head()

ID  LIMIT_BAL  SEX  EDUCATION  MARRIAGE  AGE  PAY_0  PAY_2  PAY_3  PAY_4  \
0   1      20000    2          2         1   24      2      2     -1     -1   
1   2     120000    2          2         2   26     -1      2      0      0   
2   3      90000    2          2         2   34      0      0      0      0   
3   4      50000    2          2         1   37      0      0      0      0   
4   5      50000    1          2         1   57     -1      0     -1      0   

   PAY_5  PAY_6  BILL_AMT1  BILL_AMT2  BILL_AMT3  BILL_AMT4  BILL_AMT5  \
0     -2     -2       3913       3102        689          0          0   
1      0      2       2682       1725       2682       3272       3455   
2      0      0      29239      14027      13559      14331      14948   
3      0      0      46990      48233      49291      28314      28959   
4      0      0       8617       5670      35835      20940      19146   

   BILL_AMT6  PAY_AMT1  PAY_AMT2  PAY_AMT3  PAY_AMT4  PAY_AMT5  PAY_AMT6  \
0          0         0       689         0         0         0         0   
1       3261         0      1000      1000      1000         0      2000   
2      15549      1518      1500      1000      1000      1000      5000   
3      29547      2000      2019      1200      1100      1069      1000   
4      19131      2000     36681     10000      9000       689       679   

   default payment next month  
0                           1  
1                           1  
2                           0  
3                           0  
4                           0

In [159]:
data.shape

(30000, 25)

In [160]:
print("isnull: ", data[data.isnull().any(axis=1)].shape)
print(data.isnull().any(axis=0)[data.isnull().any(axis=0)])

isnull:  (0, 25)
Series([], dtype: bool)


In [161]:
Y = data['default payment next month']
X = data.drop(columns = ['default payment next month'])

In [162]:
for c in ['SEX', 'EDUCATION', 'MARRIAGE']:
    X[c] = X[c].astype('category')

In [163]:
print([len(X[c].cat.categories) for c in X.select_dtypes('category').columns])

[2, 7, 4]


In [164]:
X.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 30000 entries, 0 to 29999
Data columns (total 24 columns):
 #   Column     Non-Null Count  Dtype   
---  ------     --------------  -----   
 0   ID         30000 non-null  int64   
 1   LIMIT_BAL  30000 non-null  int64   
 2   SEX        30000 non-null  category
 3   EDUCATION  30000 non-null  category
 4   MARRIAGE   30000 non-null  category
 5   AGE        30000 non-null  int64   
 6   PAY_0      30000 non-null  int64   
 7   PAY_2      30000 non-null  int64   
 8   PAY_3      30000 non-null  int64   
 9   PAY_4      30000 non-null  int64   
 10  PAY_5      30000 non-null  int64   
 11  PAY_6      30000 non-null  int64   
 12  BILL_AMT1  30000 non-null  int64   
 13  BILL_AMT2  30000 non-null  int64   
 14  BILL_AMT3  30000 non-null  int64   
 15  BILL_AMT4  30000 non-null  int64   
 16  BILL_AMT5  30000 non-null  int64   
 17  BILL_AMT6  30000 non-null  int64   
 18  PAY_AMT1   30000 non-null  int64   
 19  PAY_AMT2   30000 non-null

In [165]:
print({(c, X[c].unique().shape[0]) for c in X.select_dtypes(exclude='category').columns})

{('PAY_AMT2', 7899), ('PAY_5', 10), ('BILL_AMT4', 21548), ('PAY_6', 10), ('PAY_AMT3', 7518), ('PAY_3', 11), ('PAY_AMT1', 7943), ('BILL_AMT3', 22026), ('PAY_AMT5', 6897), ('BILL_AMT1', 22723), ('PAY_AMT6', 6939), ('PAY_AMT4', 6937), ('AGE', 56), ('PAY_4', 11), ('ID', 30000), ('BILL_AMT2', 22346), ('PAY_2', 11), ('PAY_0', 11), ('LIMIT_BAL', 81), ('BILL_AMT6', 20604), ('BILL_AMT5', 21010)}


In [166]:
data = Bunch(data=X, target=Y)
X, Y = preprocess(data, exclude_cols=['ID'])
with open('dataset/{}.pkl'.format(name), 'wb') as f:
    pickle.dump((X, Y), f)

(30000, 23)
isnull:  (0, 23)
Series([], dtype: bool)
isnull again:  (0, 23)
Series([], dtype: bool)
(30000, 112)


In [167]:
X

SEX=2  EDUCATION=0  EDUCATION=1  EDUCATION=2  EDUCATION=3  EDUCATION=4  \
0          1            0            0            1            0            0   
1          1            0            0            1            0            0   
2          1            0            0            1            0            0   
3          1            0            0            1            0            0   
4          0            0            0            1            0            0   
...      ...          ...          ...          ...          ...          ...   
29995      0            0            0            0            1            0   
29996      0            0            0            0            1            0   
29997      0            0            0            1            0            0   
29998      0            0            0            0            1            0   
29999      0            0            0            1            0            0   

       EDUCATION=5  EDUCATION=6  MARRIAGE=0  MARRIAGE=1  MARRIAGE=2  \
0                0            0           0           1           0   
1                0            0           0           0           1   
2                0            0           0           0           1   
3                0            0           0           1           0   
4                0            0           0           1           0   
...            ...          ...         ...         ...         ...   
29995            0            0           0           1           0   
29996            0            0           0           0           1   
29997            0            0           0           0           1   
29998            0            0           0           1           0   
29999            0            0           0           1           0   

       MARRIAGE=3  LIMIT_BAL=[10000.00-120942.15]  \
0               0                               1   
1               0                               1   
2               0                               1   
3               0                               1   
4               0                               1   
...           ...                             ...   
29995           0                               0   
29996           0                               0   
29997           0                               1   
29998           0                               1   
29999           0                               1   

       LIMIT_BAL=[120942.15-246330.41]  LIMIT_BAL=[246330.41-382782.69]  \
0                                    0                                0   
1                                    0                                0   
2                                    0                                0   
3                                    0                                0   
4                                    0                                0   
...                                ...                              ...   
29995                                1                                0   
29996                                1                                0   
29997                                0                                0   
29998                                0                                0   
29999                                0                                0   

       LIMIT_BAL=[382782.69-541397.03]  LIMIT_BAL=[541397.03-1000000.00]  \
0                                    0                                 0   
1                                    0                                 0   
2                                    0                                 0   
3                                    0                                 0   
4                                    0                                 0   
...                                ...                               ...   
29995                                0                                 0   
29996                              

In [168]:
Y

0        1
1        1
2        0
3        0
4        0
        ..
29995    0
29996    0
29997    1
29998    1
29999    1
Name: default payment next month, Length: 30000, dtype: category
Categories (2, int64): [0, 1]

## poker

In [169]:
name = 'poker'

In [170]:
data = pd.read_csv('dataset/poker-hand-testing.data', sep=",", engine='python', na_values=['?'])

In [171]:
data.columns = ['S1', 'C1', 'S2', 'C2', 'S3', 'C3', 'S4', 'C4', 'S5', 'C5'] + ['class']

In [172]:
data.head()

S1  C1  S2  C2  S3  C3  S4  C4  S5  C5  class
0   3  12   3   2   3  11   4   5   2   5      1
1   1   9   4   6   1   4   3   2   3   9      1
2   1   4   3  13   2  13   2   1   3   6      1
3   3  10   2   7   1   2   2  11   4   9      0
4   1   3   4   5   3   4   1  12   4   6      0

In [173]:
data.shape

(999999, 11)

In [174]:
print("isnull: ", data[data.isnull().any(axis=1)].shape)
print(data.isnull().any(axis=0)[data.isnull().any(axis=0)])

isnull:  (0, 11)
Series([], dtype: bool)


In [175]:
Y = data['class']
X = data.drop(columns = ['class'])

In [176]:
for c in X.columns:
    X[c] = X[c].astype('category')

In [177]:
print([len(X[c].cat.categories) for c in X.select_dtypes('category').columns])

[4, 13, 4, 13, 4, 13, 4, 13, 4, 13]


In [178]:
X.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 999999 entries, 0 to 999998
Data columns (total 10 columns):
 #   Column  Non-Null Count   Dtype   
---  ------  --------------   -----   
 0   S1      999999 non-null  category
 1   C1      999999 non-null  category
 2   S2      999999 non-null  category
 3   C2      999999 non-null  category
 4   S3      999999 non-null  category
 5   C3      999999 non-null  category
 6   S4      999999 non-null  category
 7   C4      999999 non-null  category
 8   S5      999999 non-null  category
 9   C5      999999 non-null  category
dtypes: category(10)
memory usage: 9.5 MB


In [179]:
print({(c, X[c].unique().shape[0]) for c in X.select_dtypes(exclude='category').columns})

set()


In [180]:
data = Bunch(data=X, target=Y)
X, Y = preprocess(data, exclude_cols=[])
with open('dataset/{}.pkl'.format(name), 'wb') as f:
    pickle.dump((X, Y), f)

(999999, 10)
isnull:  (0, 10)
Series([], dtype: bool)
isnull again:  (0, 10)
Series([], dtype: bool)
(999999, 85)


In [181]:
X

S1=1  S1=2  S1=3  S1=4  C1=1  C1=2  C1=3  C1=4  C1=5  C1=6  C1=7  \
0          0     0     1     0     0     0     0     0     0     0     0   
1          1     0     0     0     0     0     0     0     0     0     0   
2          1     0     0     0     0     0     0     1     0     0     0   
3          0     0     1     0     0     0     0     0     0     0     0   
4          1     0     0     0     0     0     1     0     0     0     0   
...      ...   ...   ...   ...   ...   ...   ...   ...   ...   ...   ...   
999994     0     0     1     0     1     0     0     0     0     0     0   
999995     0     0     1     0     0     0     1     0     0     0     0   
999996     1     0     0     0     0     0     0     0     0     0     0   
999997     0     0     1     0     0     0     0     0     0     0     0   
999998     0     1     0     0     0     0     0     0     1     0     0   

        C1=8  C1=9  C1=10  C1=11  C1=12  C1=13  S2=1  S2=2  S2=3  S2=4  C2=1  \
0          0     0      0      0      1      0     0     0     1     0     0   
1          0     1      0      0      0      0     0     0     0     1     0   
2          0     0      0      0      0      0     0     0     1     0     0   
3          0     0      1      0      0      0     0     1     0     0     0   
4          0     0      0      0      0      0     0     0     0     1     0   
...      ...   ...    ...    ...    ...    ...   ...   ...   ...   ...   ...   
999994     0     0      0      0      0      0     1     0     0     0     0   
999995     0     0      0      0      0      0     0     0     0     1     0   
999996     0     0      0      1      0      0     0     0     0     1     0   
999997     0     0      0      1      0      0     1     0     0     0     0   
999998     0     0      0      0      0      0     0     1     0     0     0   

        C2=2  C2=3  C2=4  C2=5  C2=6  C2=7  C2=8  C2=9  C2=10  C2=11  C2=12  \
0          1     0     0     0     0     0     0     0      0      0      0   
1          0     0     0     0     1     0     0     0      0      0      0   
2          0     0     0     0     0     0     0     0      0      0      0   
3          0     0     0     0     0     1     0     0      0      0      0   
4          0     0     0     1     0     0     0     0      0      0      0   
...      ...   ...   ...   ...   ...   ...   ...   ...    ...    ...    ...   
999994     0     0     0     0     0     0     0     0      0      0      1   
999995     0     0     0     1     0     0     0     0      0      0      0   
999996     0     0     0     0     0     1     0     0      0      0      0   
999997     0     0     0     0     0     0     1     0      0      0      0   
999998     0     0     0     0     0     0     0     1      0      0      0   

        C2=13  S3=1  S3=2  S3=3  S3=4  C3=1  C3=2  C3=3  C3=4  C3=5  C3=6  \
0           0     0     0     1     0     0     0     0     0     0     0   
1           0     1     0     0     0     0     0     0     1     0     0   
2           1     0     1     0     0     0     0     0     0     0     0   
3           0     1     0     0     0     0     1     0     0     0     0   
4           0     0     0     1     0     0     0     0     1     0     0   
...       ...   ...   ...   ...   ...   ...   ...   ...   ...   ...   ...   
999994      0     0     1     0     0     0     0     0     0     0     0   
999995      0     0     1     0     0     0     0     0     0     0     0   
999996      0     0     0     1     0     0     0     0     0     0     0   
999997      0     1     0     0     0     1     0     0     0     0     0   
999998      0     0     0     0     1     0     0     0     0     0     0   

        C3=7  C3=8  C3=9  C3=10  C3=11  C3=12  C3=13  S4=1  S4=2  S4=3  S4=4  \
0          0     0     0      0      1      0      0     0     0     0     1   
1          0     0     0      0      0      0      0     0     0     1     0   
2          0     0  

In [182]:
Y

0         1
1         1
2         1
3         0
4         0
         ..
999994    1
999995    1
999996    1
999997    1
999998    2
Name: class, Length: 999999, dtype: category
Categories (10, int64): [0, 1, 2, 3, ..., 6, 7, 8, 9]

## dota2

In [183]:
name = 'dota2'

In [184]:
data = pd.read_csv('dataset/dota2Train.csv', sep=",", engine='python', na_values=['?'])

In [185]:
data.columns = ['class', 'clusterID', 'mode', 'type'] + ['hero{}'.format(i) for i in range(113)]

In [186]:
data.head()

class  clusterID  mode  type  hero0  hero1  hero2  hero3  hero4  hero5  \
0      1        152     2     2      0      0      0      1      0     -1   
1      1        131     2     2      0      0      0      1      0     -1   
2      1        154     2     2      0      0      0      0      0      0   
3     -1        171     2     3      0      0      0      0      0     -1   
4      1        122     2     3      0      1      0      0      0      0   

   hero6  hero7  hero8  hero9  hero10  hero11  hero12  hero13  hero14  hero15  \
0      0      0      0      0       0       0       0       1       0       0   
1      0      0      0      0       0       0       0       0       0       0   
2     -1      0      0      0       0       0       0       0       0       0   
3      0      0     -1      0      -1       0       0       0       0       1   
4      0      0      0      0       0      -1       0       0       0       0   

   hero16  hero17  hero18  hero19  hero20  hero21  hero22  hero23  hero24  \
0       0       0       0       0      -1       0       0       0       0   
1       0       0       0      -1       0       1       0       0       1   
2       1       0       0       0       0       0      -1       0       0   
3       0       0       0       0       0       0       0       0       0   
4       0       0       0       0       0       0       0       0       0   

   hero25  hero26  hero27  hero28  hero29  hero30  hero31  hero32  hero33  \
0       1       1       0       0       0       0       0       0       0   
1       0       0       0       0       0       0       1       0       0   
2       0       0       0       0       0       0       0       0       0   
3       0       0       0      -1       0       1       0       0       0   
4       0       0      -1       0       0       0       0       0       0   

   hero34  hero35  hero36  hero37  hero38  hero39  hero40  hero41  hero42  \
0      -1       0       0       0       0       0       0       0       0   
1       0       0       0       0       0       0       0       0       0   
2       1       0       0       0       0       0       0      -1       0   
3       0       1       0       0       0       0       0       0       0   
4       0       0       0       0       0       0       0       0       0   

   hero43  hero44  hero45  hero46  hero47  hero48  hero49  hero50  hero51  \
0       0       0       0       0       0       0       0       0       0   
1       0       0      -1       0       0       0       0       0       0   
2       0       0       0      -1       0       0       0       0       0   
3       1       0       0       0       0       0       0       0       0   
4       0       0       0       0       0       0       0       0       0   

   hero52  hero53  hero54  hero55  hero56  hero57  hero58  hero59  hero60  \
0       0       0       0       0       0       0       0       0       0   
1       0       0       0       0       0       0       1       0       0   
2       0       1       0       0       0       0       0       0       0   
3       0       0       0       0       0       0       0       0       0   
4       0       0      -1       0       1       0       0       0       0   

   hero61  hero62  hero63  hero64  hero65  hero66  hero67  hero68  hero69  \
0       0       0       0       0       0       0       0       0       0   
1       0       0       0       0       0       0       0       0       0   
2       1       0       0       0       0       0       0       0       0   
3       0       0       0       0       0       0       0       0       0   
4       0       1       0       0       0       0       0       0      -1   

   hero70  hero71  hero72  hero73  hero74  hero75  hero76  hero77  hero78  \
0       1       0       0       0       0       0       0       0       0   
1       0      -1       0       0       0       0       0       0       0   
2       0       0       0       0       0   

In [187]:
data.shape

(92649, 117)

In [188]:
print("isnull: ", data[data.isnull().any(axis=1)].shape)
print(data.isnull().any(axis=0)[data.isnull().any(axis=0)])

isnull:  (0, 117)
Series([], dtype: bool)


In [189]:
Y = data['class']
X = data.drop(columns = ['class'])

In [190]:
for c in X.columns:
    X[c] = X[c].astype('category')

In [191]:
print([len(X[c].cat.categories) for c in X.select_dtypes('category').columns])

[47, 9, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 1, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 1, 3, 3, 3, 3, 3]


In [192]:
X.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 92649 entries, 0 to 92648
Columns: 116 entries, clusterID to hero112
dtypes: category(116)
memory usage: 10.3 MB


In [193]:
print({(c, X[c].unique().shape[0]) for c in X.select_dtypes(exclude='category').columns})

set()


In [194]:
data = Bunch(data=X, target=Y)
X, Y = preprocess(data, exclude_cols=[])
with open('dataset/{}.pkl'.format(name), 'wb') as f:
    pickle.dump((X, Y), f)

(92649, 116)
isnull:  (0, 116)
Series([], dtype: bool)
isnull again:  (0, 116)
Series([], dtype: bool)
0        0
1        0
2        0
3        0
4        0
        ..
92644    0
92645    0
92646    0
92647    0
92648    0
Name: hero23, Length: 92649, dtype: category
Categories (1, int64): [0]
0        0
1        0
2        0
3        0
4        0
        ..
92644    0
92645    0
92646    0
92647    0
92648    0
Name: hero107, Length: 92649, dtype: category
Categories (1, int64): [0]
(92649, 394)


In [195]:
X

clusterID=111  clusterID=112  clusterID=121  clusterID=122  \
0                  0              0              0              0   
1                  0              0              0              0   
2                  0              0              0              0   
3                  0              0              0              0   
4                  0              0              0              1   
...              ...            ...            ...            ...   
92644              0              0              0              0   
92645              0              0              0              0   
92646              1              0              0              0   
92647              0              0              0              0   
92648              0              0              0              0   

       clusterID=123  clusterID=124  clusterID=131  clusterID=132  \
0                  0              0              0              0   
1                  0              0              1              0   
2                  0              0              0              0   
3                  0              0              0              0   
4                  0              0              0              0   
...              ...            ...            ...            ...   
92644              0              0              0              0   
92645              0              0              0              0   
92646              0              0              0              0   
92647              0              0              0              0   
92648              0              0              0              0   

       clusterID=133  clusterID=134  clusterID=135  clusterID=136  \
0                  0              0              0              0   
1                  0              0              0              0   
2                  0              0              0              0   
3                  0              0              0              0   
4                  0              0              0              0   
...              ...            ...            ...            ...   
92644              0              0              0              0   
92645              0              0              0              0   
92646              0              0              0              0   
92647              0              0              0              0   
92648              0              0              0              0   

       clusterID=137  clusterID=138  clusterID=144  clusterID=145  \
0                  0              0              0              0   
1                  0              0              0              0   
2                  0              0              0              0   
3                  0              0              0              0   
4                  0              0              0              0   
...              ...            ...            ...            ...   
92644              0              0              0              0   
92645              0              0              0              0   
92646              0              0              0              0   
92647              0              0              0              0   
92648              0              0              0              0   

       clusterID=151  clusterID=152  clusterID=153  clusterID=154  \
0                  0              1              0              0   
1                  0              0              0              0   
2                  0              0              0              1   
3                  0              0              0              0   
4                  0              0              0              0   
...              ...            ...            ...            ...   
92644              0              0              0              1   
92645              0              0              0              1   
92646              0              0              0              0   
9

In [196]:
Y

0        1
1        1
2        1
3       -1
4        1
        ..
92644   -1
92645    1
92646    1
92647   -1
92648   -1
Name: class, Length: 92649, dtype: category
Categories (2, int64): [-1, 1]

## firewall

In [197]:
name = 'firewall'

In [198]:
data = pd.read_csv('dataset/firewall.csv', sep=",", engine='python', na_values=['?'])

In [199]:
data.columns = ['Source Port', 'Destination Port', 'NAT Source Port',
       'NAT Destination Port', 'class', 'Bytes', 'Bytes Sent',
       'Bytes Received', 'Packets', 'Elapsed Time (sec)', 'pkts_sent',
       'pkts_received']

In [200]:
data.head()

Source Port  Destination Port  NAT Source Port  NAT Destination Port  \
0        57222                53            54587                    53   
1        56258              3389            56258                  3389   
2         6881             50321            43265                 50321   
3        50553              3389            50553                  3389   
4        50002               443            45848                   443   

   class  Bytes  Bytes Sent  Bytes Received  Packets  Elapsed Time (sec)  \
0  allow    177          94              83        2                  30   
1  allow   4768        1600            3168       19                  17   
2  allow    238         118             120        2                1199   
3  allow   3327        1438            1889       15                  17   
4  allow  25358        6778           18580       31                  16   

   pkts_sent  pkts_received  
0          1              1  
1         10              9  
2          1              1  
3          8              7  
4         13             18

In [201]:
data.shape

(65532, 12)

In [202]:
print("isnull: ", data[data.isnull().any(axis=1)].shape)
print(data.isnull().any(axis=0)[data.isnull().any(axis=0)])

isnull:  (0, 12)
Series([], dtype: bool)


In [203]:
Y = data['class']
X = data.drop(columns = ['class'])

In [204]:
for c in []:
    X[c] = X[c].astype('category')

In [205]:
print([len(X[c].cat.categories) for c in X.select_dtypes('category').columns])

[]


In [206]:
X.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 65532 entries, 0 to 65531
Data columns (total 11 columns):
 #   Column                Non-Null Count  Dtype
---  ------                --------------  -----
 0   Source Port           65532 non-null  int64
 1   Destination Port      65532 non-null  int64
 2   NAT Source Port       65532 non-null  int64
 3   NAT Destination Port  65532 non-null  int64
 4   Bytes                 65532 non-null  int64
 5   Bytes Sent            65532 non-null  int64
 6   Bytes Received        65532 non-null  int64
 7   Packets               65532 non-null  int64
 8   Elapsed Time (sec)    65532 non-null  int64
 9   pkts_sent             65532 non-null  int64
 10  pkts_received         65532 non-null  int64
dtypes: int64(11)
memory usage: 5.5 MB


In [207]:
print({(c, X[c].unique().shape[0]) for c in X.select_dtypes(exclude='category').columns})

{('Bytes Received', 8814), ('Source Port', 22724), ('Destination Port', 3273), ('Elapsed Time (sec)', 915), ('Bytes', 10724), ('Packets', 1116), ('NAT Destination Port', 2533), ('pkts_received', 922), ('NAT Source Port', 29152), ('pkts_sent', 749), ('Bytes Sent', 6683)}


In [208]:
data = Bunch(data=X, target=Y)
X, Y = preprocess(data, exclude_cols=[])
with open('dataset/{}.pkl'.format(name), 'wb') as f:
    pickle.dump((X, Y), f)

(65532, 11)
isnull:  (0, 11)
Series([], dtype: bool)
isnull again:  (0, 11)
Series([], dtype: bool)
(65532, 55)


In [209]:
X

Source Port=[0.00-15269.54]  Source Port=[15269.54-31552.00]  \
0                                0                                0   
1                                0                                0   
2                                1                                0   
3                                0                                0   
4                                0                                0   
...                            ...                              ...   
65527                            0                                0   
65528                            0                                0   
65529                            0                                0   
65530                            0                                0   
65531                            0                                0   

       Source Port=[31552.00-45536.14]  Source Port=[45536.14-56362.93]  \
0                                    0                                0   
1                                    0                                1   
2                                    0                                0   
3                                    0                                1   
4                                    0                                1   
...                                ...                              ...   
65527                                0                                0   
65528                                0                                1   
65529                                0                                1   
65530                                0                                1   
65531                                0                                1   

       Source Port=[56362.93-65534.00]  Destination Port=[0.00-11813.41]  \
0                                    1                                 1   
1                                    0                                 1   
2                                    0                                 0   
3                                    0                                 1   
4                                    0                                 1   
...                                ...                               ...   
65527                                1                                 1   
65528                                0                                 1   
65529                                0                                 1   
65530                                0                                 1   
65531                                0                                 1   

       Destination Port=[11813.41-29363.18]  \
0                                         0   
1                                         0   
2                                         0   
3                                         0   
4                                         0   
...                                     ...   
65527                                     0   
65528                                     0   
65529                                     0   
65530                                     0   
65531                                     0   

       Destination Port=[29363.18-42215.53]  \
0                                         0   
1                                         0   
2                                         0   
3                                         0   
4                                         0   
...                                     ...   
65527                                     0   
65528                                     0   
65529                                     0   
65530                                     0   
65531                                     0   

       Destination Port=[42215.53-54320.36]  \
0                                         0   
1                                         0   
2                                         1   
3                     

In [210]:
Y

0        allow
1        allow
2        allow
3        allow
4        allow
         ...  
65527    allow
65528    allow
65529     drop
65530     drop
65531     drop
Name: class, Length: 65532, dtype: category
Categories (4, object): ['allow', 'deny', 'drop', 'reset-both']

## obesity

In [211]:
name = 'obesity'

In [212]:
data = pd.read_csv('dataset/ObesityDataSet_raw_and_data_sinthetic.csv', sep=",", engine='python', na_values=['?'])

In [213]:
data.columns = data.columns[:-1].to_list() + ['class']

In [214]:
data.head()

Gender   Age  Height  Weight family_history_with_overweight FAVC  FCVC  \
0  Female  21.0    1.62    64.0                            yes   no   2.0   
1  Female  21.0    1.52    56.0                            yes   no   3.0   
2    Male  23.0    1.80    77.0                            yes   no   2.0   
3    Male  27.0    1.80    87.0                             no   no   3.0   
4    Male  22.0    1.78    89.8                             no   no   2.0   

   NCP       CAEC SMOKE  CH2O  SCC  FAF  TUE        CALC  \
0  3.0  Sometimes    no   2.0   no  0.0  1.0          no   
1  3.0  Sometimes   yes   3.0  yes  3.0  0.0   Sometimes   
2  3.0  Sometimes    no   2.0   no  2.0  1.0  Frequently   
3  3.0  Sometimes    no   2.0   no  2.0  0.0  Frequently   
4  1.0  Sometimes    no   2.0   no  0.0  0.0   Sometimes   

                  MTRANS                class  
0  Public_Transportation        Normal_Weight  
1  Public_Transportation        Normal_Weight  
2  Public_Transportation        Normal_Weight  
3                Walking   Overweight_Level_I  
4  Public_Transportation  Overweight_Level_II

In [215]:
data.shape

(2111, 17)

In [216]:
print("isnull: ", data[data.isnull().any(axis=1)].shape)
print(data.isnull().any(axis=0)[data.isnull().any(axis=0)])

isnull:  (0, 17)
Series([], dtype: bool)


In [217]:
Y = data['class']
X = data.drop(columns = ['class'])

In [218]:
for c in X.select_dtypes('object'):
    X[c] = X[c].astype('category')

In [219]:
print([len(X[c].cat.categories) for c in X.select_dtypes('category').columns])

[2, 2, 2, 4, 2, 2, 4, 5]


In [220]:
X.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2111 entries, 0 to 2110
Data columns (total 16 columns):
 #   Column                          Non-Null Count  Dtype   
---  ------                          --------------  -----   
 0   Gender                          2111 non-null   category
 1   Age                             2111 non-null   float64 
 2   Height                          2111 non-null   float64 
 3   Weight                          2111 non-null   float64 
 4   family_history_with_overweight  2111 non-null   category
 5   FAVC                            2111 non-null   category
 6   FCVC                            2111 non-null   float64 
 7   NCP                             2111 non-null   float64 
 8   CAEC                            2111 non-null   category
 9   SMOKE                           2111 non-null   category
 10  CH2O                            2111 non-null   float64 
 11  SCC                             2111 non-null   category
 12  FAF                 

In [221]:
print({(c, X[c].unique().shape[0]) for c in X.select_dtypes(exclude='category').columns})

{('Height', 1574), ('Weight', 1525), ('FCVC', 810), ('FAF', 1190), ('TUE', 1129), ('Age', 1402), ('CH2O', 1268), ('NCP', 635)}


In [222]:
data = Bunch(data=X, target=Y)
X, Y = preprocess(data, exclude_cols=[])
with open('dataset/{}.pkl'.format(name), 'wb') as f:
    pickle.dump((X, Y), f)

(2111, 16)
isnull:  (0, 16)
Series([], dtype: bool)
isnull again:  (0, 16)
Series([], dtype: bool)
(2111, 58)


In [223]:
X

Gender=Male  family_history_with_overweight=yes  FAVC=yes  CAEC=Always  \
0               0                                   1         0            0   
1               0                                   1         0            0   
2               1                                   1         0            0   
3               1                                   0         0            0   
4               1                                   0         0            0   
...           ...                                 ...       ...          ...   
2106            0                                   1         1            0   
2107            0                                   1         1            0   
2108            0                                   1         1            0   
2109            0                                   1         1            0   
2110            0                                   1         1            0   

      CAEC=Frequently  CAEC=Sometimes  CAEC=no  SMOKE=yes  SCC=yes  \
0                   0               1        0          0        0   
1                   0               1        0          1        1   
2                   0               1        0          0        0   
3                   0               1        0          0        0   
4                   0               1        0          0        0   
...               ...             ...      ...        ...      ...   
2106                0               1        0          0        0   
2107                0               1        0          0        0   
2108                0               1        0          0        0   
2109                0               1        0          0        0   
2110                0               1        0          0        0   

      CALC=Always  CALC=Frequently  CALC=Sometimes  CALC=no  \
0               0                0               0        1   
1               0                0               1        0   
2               0                1               0        0   
3               0                1               0        0   
4               0                0               1        0   
...           ...              ...             ...      ...   
2106            0                0               1        0   
2107            0                0               1        0   
2108            0                0               1        0   
2109            0                0               1        0   
2110            0                0               1        0   

      MTRANS=Automobile  MTRANS=Bike  MTRANS=Motorbike  \
0                     0            0                 0   
1                     0            0                 0   
2                     0            0                 0   
3                     0            0                 0   
4                     0            0                 0   
...                 ...          ...               ...   
2106                  0            0                 0   
2107                  0            0                 0   
2108                  0            0                 0   
2109                  0            0                 0   
2110                  0            0                 0   

      MTRANS=Public_Transportation  MTRANS=Walking  Age=[14.00-22.10]  \
0                                1               0                  1   
1                                1               0                  1   
2                                1               0                  0   
3                                0               1                  0   
4                                1               0                  1   
...                            ...             ...                ...   
2106                             1               0                  1   
2107                             1               0                  1   
2108                             1               0                  0   
2109                

In [224]:
Y

0             Normal_Weight
1             Normal_Weight
2             Normal_Weight
3        Overweight_Level_I
4       Overweight_Level_II
               ...         
2106       Obesity_Type_III
2107       Obesity_Type_III
2108       Obesity_Type_III
2109       Obesity_Type_III
2110       Obesity_Type_III
Name: class, Length: 2111, dtype: category
Categories (7, object): ['Insufficient_Weight', 'Normal_Weight', 'Obesity_Type_I', 'Obesity_Type_II', 'Obesity_Type_III', 'Overweight_Level_I', 'Overweight_Level_II']